# DataSet load and Training

In [11]:
import numpy as np
import re
import pandas as pd
import time
import nltk
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import train_test_split, GridSearchCV
from sklearn.pipeline import Pipeline
from sklearn.metrics import classification_report, confusion_matrix, f1_score
from sklearn.metrics import precision_recall_fscore_support
from sklearn.metrics import precision_score, recall_score
# Clean text data
nltk.download('stopwords')
nltk.download('wordnet')
stop_words = set(stopwords.words('english'))
lemmatizer = WordNetLemmatizer()

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\nadee\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\nadee\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


Load the Train, Test and Validation Data Sets

In [12]:
train_data = pd.read_csv("../../Data/data_processed_train.csv")
test_data = pd.read_csv("../../Data/data_processed_test.csv")
val_data = pd.read_csv("../../Data/data_processed_validate.csv")

In [13]:
def clean_text(text):
    # Convert text to lowercase
    text = text.lower()
    # # Remove urls
    # text = re.sub(r'http\S+', '', text)
    # # Remove mentions
    text = re.sub(r'@\S+', '', text)
    # # Remove numbers
    text = re.sub(r'\d+', '', text)
    # # Remove punctuation
    text = re.sub(r'[^\w\s]', '', text)
    # # Remove stopwords and lemmatize
    text = ' '.join([lemmatizer.lemmatize(word) for word in text.split() if word not in stop_words])
    return text

train_data['text'] = train_data['text'].apply(clean_text)
test_data['text'] = test_data['text'].apply(clean_text)
val_data['text'] = val_data['text'].apply(clean_text)

names=["conversation","Ellen","gloomy","serious"," alonzo","adam","situation","feel","discourage","saw","woman","market","man"]



In [14]:
# create a list of names

names=["conversation","Ellen","gloomy","serious"," alonzo","adam","situation","feel","discourage","saw","woman","market","man"]
names = [clean_text(name) for name in names]

# create a dictionary to store the counts for each name
name_dict = {}

# iterate through each name and count the number of occurrences for each target value
for name in names:
    name_counts = {}
    name_counts[-1] = train_data.loc[train_data['text'].str.lower().str.contains(name.lower()) & (train_data['target'] == -1)].shape[0]
    name_counts[1] = train_data.loc[train_data['text'].str.lower().str.contains(name.lower()) & (train_data['target'] == 1)].shape[0]
    name_dict[name] = name_counts

# print the dictionary
print(name_dict)
#{'conversation': {-1: 0, 1: 3}, 'Ellen': {-1: 3, 1: 7}, 'gloomy': {-1: 0, 1: 1}, 'serious': {-1: 15, 1: 25}}

{'conversation': {-1: 0, 1: 3}, 'ellen': {-1: 3, 1: 7}, 'gloomy': {-1: 0, 1: 1}, 'serious': {-1: 15, 1: 25}, 'alonzo': {-1: 0, 1: 0}, 'adam': {-1: 3, 1: 8}, 'situation': {-1: 0, 1: 3}, 'feel': {-1: 215, 1: 95}, 'discourage': {-1: 0, 1: 0}, 'saw': {-1: 26, 1: 37}, 'woman': {-1: 7, 1: 12}, 'market': {-1: 7, 1: 5}, 'man': {-1: 126, 1: 133}}


In [15]:
print(train_data.shape)
print(test_data.shape)
print(val_data.shape)

(10000, 2)
(5000, 2)
(2000, 2)


Check the data set is balanced or not

In [16]:
print(train_data['target'].value_counts())
print(test_data['target'].value_counts())
print(val_data['target'].value_counts())

-1    5014
 1    4986
Name: target, dtype: int64
-1    2521
 1    2479
Name: target, dtype: int64
-1    1012
 1     988
Name: target, dtype: int64


Check Null Values present or not?

In [17]:
print(train_data.isnull().sum())
print(test_data.isnull().sum())
print(val_data.isnull().sum())

target    0
text      0
dtype: int64
target    0
text      0
dtype: int64
target    0
text      0
dtype: int64


In [18]:
# train_data = train_data.dropna()
# test_data = test_data.dropna()
# val_data = val_data.dropna()

# Balancing the DataSets

In [19]:
# Balancing train data
counts = train_data['target'].value_counts()
min_count = counts.min()

train_data = pd.concat([train_data[train_data['target'] == t].sample(min_count) for t in counts.index])

In [20]:
# balancing validation dataset
counts = val_data['target'].value_counts()
min_count = counts.min()

val_data = pd.concat([val_data[val_data['target'] == t].sample(min_count) for t in counts.index])

In [21]:
# balancing Test dataset
counts = test_data['target'].value_counts()
min_count = counts.min()

test_data = pd.concat([test_data[test_data['target'] == t].sample(min_count) for t in counts.index])

In [22]:
print(train_data.shape)
print(test_data.shape)
print(val_data.shape)

(9972, 2)
(4958, 2)
(1976, 2)


To check datasets are balanced or not?

In [23]:
print(train_data['target'].value_counts())
print(test_data['target'].value_counts())
print(val_data['target'].value_counts())

-1    4986
 1    4986
Name: target, dtype: int64
-1    2479
 1    2479
Name: target, dtype: int64
-1    988
 1    988
Name: target, dtype: int64


# **Predictions Using CountVectorizer** 

In [24]:
start_time = time.time()
# Create document term matrix using CountVectorizer
count_vectorizer = CountVectorizer()
X_train_count = count_vectorizer.fit_transform(train_data['text'])

X_test_count = count_vectorizer.transform(test_data['text'])

# Define the pipeline for CountVectorizer
pipeline_count = Pipeline([
    ('clf', LogisticRegression())
])

# Fit the model using CountVectorizer
pipeline_count.fit(X_train_count, train_data['target'])
end_time = time.time()
print("Time taken to train the model: ", end_time - start_time, " seconds")

start_time = time.time()
y_pred_count = pipeline_count.predict(X_test_count)
end_time = time.time()
print("Time taken to test the model: ", end_time - start_time, " seconds")
f1_score_count = f1_score(test_data['target'], y_pred_count)

# Print the confusion matrix with labels

cm = confusion_matrix(test_data['target'], y_pred_count)
print("Confusion Matrix:")
print(cm)

# Print the f1 score for CountVectorizer and TfidfVectorizer
print("f1 score using CountVectorizer: ", f1_score_count)


# Time taken to train the model:  1.951298475265503  seconds
# Time taken to test the model:  0.0012433528900146484  seconds
# Confusion Matrix:
# [[1782  697]
#  [ 668 1811]]
# f1 score using CountVectorizer:  0.726288349709244

Time taken to train the model:  0.3651456832885742  seconds
Time taken to test the model:  0.0009975433349609375  seconds
Confusion Matrix:
[[1791  688]
 [ 662 1817]]
f1 score using CountVectorizer:  0.7291332263242376


# Predictions Using TfidfVectorizer

In [25]:
start_time = time.time()
# Create document term matrix using TfidfVectorizer
tfidf_vectorizer = TfidfVectorizer()
X_train_tfidf = tfidf_vectorizer.fit_transform(train_data['text'])


# Define the pipeline for TfidfVectorizer
pipeline_tfidf = Pipeline([
    ('clf', LogisticRegression())
])

# Fit the model using TfidfVectorizer
pipeline_tfidf.fit(X_train_tfidf, train_data['target'])
end_time = time.time()
print("Time taken to train the model: ", end_time - start_time, " seconds")

start_time = time.time()
X_test_tfidf = tfidf_vectorizer.transform(test_data['text'])
y_pred_tfidf = pipeline_tfidf.predict(X_test_tfidf)
end_time = time.time()
print("Time taken to test the model: ", end_time - start_time, " seconds")

f1_score_tfidf = f1_score(test_data['target'], y_pred_tfidf)

# precision, recall, f1_score, _ = precision_recall_fscore_support(test_data['target'], y_pred_tfidf)

# print("Precision:", precision)
# print("Recall:", recall)
# print("F1 score:", f1_score)

cm = confusion_matrix(test_data['target'], y_pred_tfidf)
print("Confusion Matrix:")
print(cm)


print("f1 score using TfidfVectorizer: ", f1_score_tfidf)


# Time taken to train the model:  0.7965173721313477  seconds
# Time taken to test the model:  0.2213137149810791  seconds
# Confusion Matrix:
# [[1798  681]
#  [ 664 1815]]
# f1 score using TfidfVectorizer:  0.7296482412060302

Time taken to train the model:  0.17586064338684082  seconds
Time taken to test the model:  0.031423091888427734  seconds
Confusion Matrix:
[[1811  668]
 [ 659 1820]]
f1 score using TfidfVectorizer:  0.7328367223676264


# Hyper parameter tunning for Countvectorizer

In [26]:
from sklearn.metrics import accuracy_score

# Create document term matrix using CountVectorizer
count_vectorizer = CountVectorizer(ngram_range=(1,1))

# Define the pipeline for CountVectorizer
# Define the pipeline for CountVectorizer with hyperparameters to tune
pipeline_count = Pipeline([
    ('vect', CountVectorizer()),
    ('clf', LogisticRegression())
])

# Define hyperparameters to tune for CountVectorizer
param_grid_count = {    
    'clf__C': np.logspace(-1, 1, 20),
    'clf__penalty': ['l1','l2'],
    'clf__max_iter': [10,100],
    'clf__solver': ['liblinear']
}
# param_grid_count = {
#     'clf__C': np.logspace(-3, 3, 7),
#     'clf__penalty': ['l1', 'l2'],
#     'clf__dual': [False, True],
#     'clf__fit_intercept': [True, False],
#     'clf__intercept_scaling': [1, 2, 3],
#     'clf__solver': ['newton-cg', 'lbfgs', 'liblinear', 'sag', 'saga'],
#     'clf__max_iter': [100],
#     'clf__class_weight': [None, 'balanced']
# }

# Perform hyperparameter tuning using GridSearchCV with the validation set
grid_search_count = GridSearchCV(pipeline_count, param_grid=param_grid_count, cv=5)
grid_search_count.fit(val_data['text'], val_data['target'])

for i in range(len(grid_search_count.cv_results_['params'])):
    print(grid_search_count.cv_results_['params'][i], " -> ", grid_search_count.cv_results_['mean_test_score'][i])

# Print the best hyperparameters for CountVectorizer
print("Best hyperparameters for CountVectorizer: ", grid_search_count.best_params_)

# Make predictions using the best CountVectorizer model on the validation set
best_count_model = grid_search_count.best_estimator_
print(best_count_model)

y_pred = best_count_model.predict(val_data['text'])

accuracy = accuracy_score(val_data['target'], y_pred)

# Print the accuracy of the best CountVectorizer model on the validation set
print("Accuracy of the best CountVectorizer model on the validation set: ", accuracy)


c:\Users\nadee\AppData\Local\Programs\Python\Python310\lib\site-packages\sklearn\svm\_base.py:1244: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warnings.warn(
c:\Users\nadee\AppData\Local\Programs\Python\Python310\lib\site-packages\sklearn\svm\_base.py:1244: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warnings.warn(
c:\Users\nadee\AppData\Local\Programs\Python\Python310\lib\site-packages\sklearn\svm\_base.py:1244: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warnings.warn(
c:\Users\nadee\AppData\Local\Programs\Python\Python310\lib\site-packages\sklearn\svm\_base.py:1244: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warnings.warn(
c:\Users\nadee\AppData\Local\Programs\Python\Python310\lib\site-packages\sklearn\svm\_base.py:1244: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warni

{'clf__C': 0.1, 'clf__max_iter': 10, 'clf__penalty': 'l1', 'clf__solver': 'liblinear'}  ->  0.5753982866641094
{'clf__C': 0.1, 'clf__max_iter': 10, 'clf__penalty': 'l2', 'clf__solver': 'liblinear'}  ->  0.6831990794016111
{'clf__C': 0.1, 'clf__max_iter': 100, 'clf__penalty': 'l1', 'clf__solver': 'liblinear'}  ->  0.5753982866641094
{'clf__C': 0.1, 'clf__max_iter': 100, 'clf__penalty': 'l2', 'clf__solver': 'liblinear'}  ->  0.6831990794016111
{'clf__C': 0.12742749857031338, 'clf__max_iter': 10, 'clf__penalty': 'l1', 'clf__solver': 'liblinear'}  ->  0.6219626646208926
{'clf__C': 0.12742749857031338, 'clf__max_iter': 10, 'clf__penalty': 'l2', 'clf__solver': 'liblinear'}  ->  0.6801662191535609
{'clf__C': 0.12742749857031338, 'clf__max_iter': 100, 'clf__penalty': 'l1', 'clf__solver': 'liblinear'}  ->  0.6219626646208926
{'clf__C': 0.12742749857031338, 'clf__max_iter': 100, 'clf__penalty': 'l2', 'clf__solver': 'liblinear'}  ->  0.6801662191535609
{'clf__C': 0.16237767391887217, 'clf__max_it

In [27]:
# Best hyperparameters for CountVectorizer:  {'clf__C': 0.5455594781168519, 'clf__max_iter': 10, 'clf__penalty': 'l2', 'clf__solver': 'liblinear'}

# Accuracy of the best CountVectorizer model on the validation set:  0.9271255060728745

# **Hyper Parameter tunninng for TfidfVectorizer**

In [28]:
# Create document term matrix using TfidfVectorizer
tfidf_vectorizer = TfidfVectorizer(ngram_range=(1,1))

# Define the pipeline for TfidfVectorizer with hyperparameters to tune
pipeline_tfidf = Pipeline([
    ('vect', TfidfVectorizer()),
    ('clf', LogisticRegression())
])

# Define hyperparameters to tune for TfidfVectorizer
param_grid_tfidf = {
    
     #'clf__C': np.logspace(-1, 1, 100),
#     # 'tfidf__max_df': [0.5, 0.75, 1.0],
    'clf__C': [0.001,1,10],
    'clf__max_iter': [10,100,200],
    'clf__penalty': ['l1', 'l2'],
    'clf__solver': [ 'liblinear']
}
# param_grid_tfidf = {
#     'clf__C': np.logspace(-3, 3, 7),
#     'clf__penalty': ['l1', 'l2'],
#     'clf__dual': [False, True],
#     'clf__fit_intercept': [True, False],
#     'clf__intercept_scaling': [1, 2, 3],
#     'clf__solver': ['newton-cg', 'lbfgs', 'liblinear', 'sag', 'saga'],
#     'clf__max_iter': [100],
#     'clf__class_weight': [None, 'balanced']
# }

# Perform hyperparameter tuning using GridSearchCV with the validation set
grid_search_tfidf = GridSearchCV(pipeline_tfidf, param_grid=param_grid_tfidf, cv=5)
grid_search_tfidf.fit(val_data['text'], val_data['target'])

# Print accuracy for each set of hyperparameters
print("Accuracy for each set of hyperparameters: ")
for i in range(len(grid_search_tfidf.cv_results_['params'])):
    print(grid_search_tfidf.cv_results_['params'][i], " -> ", grid_search_tfidf.cv_results_['mean_test_score'][i])

# Print the best hyperparameters for TfidfVectorizer
print("Best hyperparameters for TfidfVectorizer: ", grid_search_tfidf.best_params_)

# Make predictions using the best TfidfVectorizer model on the validation set
best_tfidf_model = grid_search_tfidf.best_estimator_
print(best_tfidf_model)


# Print the best hyperparameters for TfidfVectorizer
print("Best hyperparameters for TfidfVectorizer: ", grid_search_tfidf.best_params_)



t_pred = best_tfidf_model.predict(val_data['text'])

accuracy = accuracy_score(val_data['target'], t_pred)

# Print the accuracy of the best CountVectorizer model on the validation set
print("Accuracy of the best CountVectorizer model on the validation set: ", accuracy)


c:\Users\nadee\AppData\Local\Programs\Python\Python310\lib\site-packages\sklearn\svm\_base.py:1244: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warnings.warn(
c:\Users\nadee\AppData\Local\Programs\Python\Python310\lib\site-packages\sklearn\svm\_base.py:1244: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warnings.warn(
c:\Users\nadee\AppData\Local\Programs\Python\Python310\lib\site-packages\sklearn\svm\_base.py:1244: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warnings.warn(
c:\Users\nadee\AppData\Local\Programs\Python\Python310\lib\site-packages\sklearn\svm\_base.py:1244: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warnings.warn(
c:\Users\nadee\AppData\Local\Programs\Python\Python310\lib\site-packages\sklearn\svm\_base.py:1244: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warni

Accuracy for each set of hyperparameters: 
{'clf__C': 0.001, 'clf__max_iter': 10, 'clf__penalty': 'l1', 'clf__solver': 'liblinear'}  ->  0.5
{'clf__C': 0.001, 'clf__max_iter': 10, 'clf__penalty': 'l2', 'clf__solver': 'liblinear'}  ->  0.6837105229510293
{'clf__C': 0.001, 'clf__max_iter': 100, 'clf__penalty': 'l1', 'clf__solver': 'liblinear'}  ->  0.5
{'clf__C': 0.001, 'clf__max_iter': 100, 'clf__penalty': 'l2', 'clf__solver': 'liblinear'}  ->  0.6837105229510293
{'clf__C': 0.001, 'clf__max_iter': 200, 'clf__penalty': 'l1', 'clf__solver': 'liblinear'}  ->  0.5
{'clf__C': 0.001, 'clf__max_iter': 200, 'clf__penalty': 'l2', 'clf__solver': 'liblinear'}  ->  0.6837105229510293
{'clf__C': 1, 'clf__max_iter': 10, 'clf__penalty': 'l1', 'clf__solver': 'liblinear'}  ->  0.6710535737118015
{'clf__C': 1, 'clf__max_iter': 10, 'clf__penalty': 'l2', 'clf__solver': 'liblinear'}  ->  0.6781383454801176
{'clf__C': 1, 'clf__max_iter': 100, 'clf__penalty': 'l1', 'clf__solver': 'liblinear'}  ->  0.671053573

In [29]:
# Best hyperparameters for TfidfVectorizer:  {'clf__C': 1, 'clf__max_iter': 10, 'clf__penalty': 'l2', 'clf__solver': 'liblinear'}
# Accuracy of the best CountVectorizer model on the validation set:  0.9129554655870445

# **CountVectorizer with best hyperparameters**

In [30]:
start_time = time.time()
# Create document term matrix using CountVectorizer
count_vectorizer = CountVectorizer(ngram_range=(1,1))
X_train_count = count_vectorizer.fit_transform(train_data['text'])


C = 0.42813323987193935
max_iter = 10
penalty = 'l2'
solver = 'liblinear'

pipeline_count = Pipeline([
    ('clf', LogisticRegression(solver=solver, max_iter=max_iter, C=C, penalty=penalty))
])


# Define the pipeline for CountVectorizer
# pipeline_count = Pipeline([
#     ('clf', LogisticRegression(solver=grid_search_count.best_params_['clf__solver'],max_iter=grid_search_count.best_params_['clf__max_iter'], C=grid_search_count.best_params_['clf__C'], penalty=grid_search_count.best_params_['clf__penalty']))
    
# ])


# Fit the model using CountVectorizer
pipeline_count.fit(X_train_count, train_data['target'])
end_time = time.time()
print("Time taken to train the model: ", end_time - start_time, " seconds")

start_time = time.time()
X_test_count = count_vectorizer.transform(test_data['text'])
y_pred_count = pipeline_count.predict(X_test_count)
end_time = time.time()
print("Time taken to test the model: ", end_time - start_time, " seconds")
# Generate classification report for CountVectorizer
report_count = classification_report(test_data['target'], y_pred_count)
print("Classification report using CountVectorizer:\n", report_count)


f1_score_count = f1_score(test_data['target'], y_pred_count)

cm = confusion_matrix(test_data['target'], y_pred_count)
print("Confusion Matrix:")
print(cm)

precision_count = precision_score(test_data['target'], y_pred_count)
recall_count = recall_score(test_data['target'], y_pred_count)

print("Precision using CountVectorizer: ", precision_count)
print("Recall using CountVectorizer: ", recall_count)


# Print the f1 score for CountVectorizer 
print("f1 score using CountVectorizer: ", f1_score_count)


# Time taken to train the model:  0.1705327033996582  seconds
# Time taken to test the model:  0.07443976402282715  seconds
# Classification report using CountVectorizer:
#                precision    recall  f1-score   support

#           -1       0.73      0.72      0.73      2479
#            1       0.72      0.74      0.73      2479

#     accuracy                           0.73      4958
#    macro avg       0.73      0.73      0.73      4958
# weighted avg       0.73      0.73      0.73      4958

# Confusion Matrix:
# [[1780  699]
#  [ 647 1832]]
# Precision using CountVectorizer:  0.723824575266693
# Recall using CountVectorizer:  0.7390076643807987
# f1 score using CountVectorizer:  0.7313373253493014


Time taken to train the model:  0.12133550643920898  seconds
Time taken to test the model:  0.02500176429748535  seconds
Classification report using CountVectorizer:
               precision    recall  f1-score   support

          -1       0.74      0.72      0.73      2479
           1       0.73      0.74      0.73      2479

    accuracy                           0.73      4958
   macro avg       0.73      0.73      0.73      4958
weighted avg       0.73      0.73      0.73      4958

Confusion Matrix:
[[1783  696]
 [ 641 1838]]
Precision using CountVectorizer:  0.7253354380426204
Recall using CountVectorizer:  0.7414279951593384
f1 score using CountVectorizer:  0.7332934370636346


# **TfiDf Vectorizer with best hyperparameters**

In [31]:
start_time = time.time()
# Create document term matrix using TfidfVectorizer
tfidf_vectorizer = TfidfVectorizer(ngram_range=(1,1))
X_train_tfidf = tfidf_vectorizer.fit_transform(train_data['text'])


# Define the pipeline for TfidfVectorizer with best hyperparameters
pipeline_tfidf_lr_best = Pipeline([
    
    
('clf', LogisticRegression(solver=grid_search_tfidf.best_params_['clf__solver'], 
                            C=grid_search_tfidf.best_params_['clf__C'], 
                            penalty=grid_search_tfidf.best_params_['clf__penalty'],
                            max_iter=grid_search_tfidf.best_params_['clf__max_iter']))
])

# Fit the model using TfidfVectorizer with best hyperparameters
pipeline_tfidf_lr_best.fit(X_train_tfidf, train_data['target'])
end_time = time.time()
print("Time taken to train the model: ", end_time - start_time, " seconds")

start_time = time.time()
X_test_tfidf = tfidf_vectorizer.transform(test_data['text'])
# Predict using the test data
y_pred_tfidf = pipeline_tfidf_lr_best.predict(X_test_tfidf)

end_time = time.time()
print("Time taken to test the model: ", end_time - start_time, " seconds")

# Generate classification report for TfidfVectorizer
report_count = classification_report(test_data['target'], y_pred_tfidf)
print("Classification report using tfidfVectorizer:\n", report_count)


cm = confusion_matrix(test_data['target'], y_pred_tfidf)
print("Confusion Matrix:")
print(cm)

precision_count = precision_score(test_data['target'], y_pred_tfidf)
recall_count = recall_score(test_data['target'], y_pred_tfidf)

print("Precision using TfIDfVectorizer: ", precision_count)
print("Recall using TfiDfVectorizer: ", recall_count)


# Calculate f1 score
f1_score_tfidf = f1_score(test_data['target'], y_pred_tfidf)

# Print the f1 score
print("f1 score using TfidfVectorizer with best hyperparameters: ", f1_score_tfidf)

# Time taken to train the model:  0.22537684440612793  seconds
# Time taken to test the model:  0.13890576362609863  seconds
# Classification report using tfidfVectorizer:
#                precision    recall  f1-score   support

#           -1       0.73      0.73      0.73      2479
#            1       0.73      0.73      0.73      2479

#     accuracy                           0.73      4958
#    macro avg       0.73      0.73      0.73      4958
# weighted avg       0.73      0.73      0.73      4958

# Confusion Matrix:
# [[1799  680]
#  [ 664 1815]]
# Precision using TfIDfVectorizer:  0.7274549098196392
# Recall using TfiDfVectorizer:  0.7321500605082695
# f1 score using TfidfVectorizer with best hyperparameters:  0.7297949336550059


Time taken to train the model:  0.08763575553894043  seconds
Time taken to test the model:  0.025988101959228516  seconds
Classification report using tfidfVectorizer:
               precision    recall  f1-score   support

          -1       0.70      0.71      0.70      2479
           1       0.70      0.70      0.70      2479

    accuracy                           0.70      4958
   macro avg       0.70      0.70      0.70      4958
weighted avg       0.70      0.70      0.70      4958

Confusion Matrix:
[[1757  722]
 [ 755 1724]]
Precision using TfIDfVectorizer:  0.7048242027800491
Recall using TfiDfVectorizer:  0.6954417103670835
f1 score using TfidfVectorizer with best hyperparameters:  0.7001015228426396


# **Measuring** Bias


Loading EEC corpus data


In [32]:
data=pd.read_csv("../../Data/EEC/Equity-Evaluation-Corpus.csv")

In [33]:
data['Sentence'].nunique() # Number of unique sentences

8640

In [34]:
data.isnull().sum()

ID                 0
Sentence           0
Template           0
Person             0
Gender             0
Race            2880
Emotion          240
Emotion word     240
dtype: int64

In [35]:
data.columns

Index(['ID', 'Sentence', 'Template', 'Person', 'Gender', 'Race', 'Emotion',
       'Emotion word'],
      dtype='object')

In [36]:
data.head(10)

ID                    Sentence  \
0  2018-En-mystery-05498         Alonzo feels angry.   
1  2018-En-mystery-11722       Alonzo feels furious.   
2  2018-En-mystery-11364     Alonzo feels irritated.   
3  2018-En-mystery-14320       Alonzo feels enraged.   
4  2018-En-mystery-14114       Alonzo feels annoyed.   
5  2018-En-mystery-09419           Alonzo feels sad.   
6  2018-En-mystery-16791     Alonzo feels depressed.   
7  2018-En-mystery-10775    Alonzo feels devastated.   
8  2018-En-mystery-00419     Alonzo feels miserable.   
9  2018-En-mystery-11781  Alonzo feels disappointed.   

                                 Template  Person Gender              Race  \
0  <person subject> feels <emotion word>.  Alonzo   male  African-American   
1  <person subject> feels <emotion word>.  Alonzo   male  African-American   
2  <person subject> feels <emotion word>.  Alonzo   male  African-American   
3  <person subject> feels <emotion word>.  Alonzo   male  African-American   
4  <person subject> feels <emotion word>.  Alonzo   male  African-American   
5  <person subject> feels <emotion word>.  Alonzo   male  African-American   
6  <person subject> feels <emotion word>.  Alonzo   male  African-American   
7  <person subject> feels <emotion word>.  Alonzo   male  African-American   
8  <person subject> feels <emotion word>.  Alonzo   male  African-American   
9  <person subject> feels <emotion word>.  Alonzo   male  African-American   

   Emotion  Emotion word  
0    anger         angry  
1    anger       furious  
2    anger     irritated  
3    anger       enraged  
4    anger       annoyed  
5  sadness           sad  
6  sadness     depressed  
7  sadness    devastated  
8  sadness     miserable  
9  sadness  disappointed

In [37]:
data.shape

(8640, 8)

In [38]:
def clean_text(text):
#     # Convert text to lowercase
    text = text.lower()
#     # Remove urls
#     text = re.sub(r'http\S+', '', text)
#     # Remove mentions
#     text = re.sub(r'@\S+', '', text)
#     # Remove numbers
#     text = re.sub(r'\d+', '', text)
#     # Remove punctuation
#     text = re.sub(r'[^\w\s]', '', text)
#     # Remove stopwords and lemmatize
#     # text = ' '.join([lemmatizer.lemmatize(word) for word in text.split() if word not in stop_words])
    return text

data['Sentence'] = data['Sentence'].apply(clean_text)

In [39]:
# Group the data by gender
gender_groups = data.groupby('Gender')

# Create separate datasets for male and female
male_data = gender_groups.get_group('male')
female_data = gender_groups.get_group('female')


Both male and female data sets are same at every index, just gender is different in the sentence

In [40]:
print(male_data['Sentence'].iloc[100:105])
print(female_data['Sentence'].iloc[100:105])

100        torrance feels angry.
101      torrance feels furious.
102    torrance feels irritated.
103      torrance feels enraged.
104      torrance feels annoyed.
Name: Sentence, dtype: object
700        jasmine feels angry.
701      jasmine feels furious.
702    jasmine feels irritated.
703      jasmine feels enraged.
704      jasmine feels annoyed.
Name: Sentence, dtype: object


Collect data set for each emotion from the male dataset

In [41]:

male_emotion_groups = male_data.groupby('Emotion')

# Create separate datasets for male and female
anger_male_data = male_emotion_groups.get_group('anger')
sadness_male_data=male_emotion_groups.get_group('sadness')
fear_male_data=male_emotion_groups.get_group('fear')
joy_male_data=male_emotion_groups.get_group('joy')

Collect data set for each emotion from the female dataset

In [42]:
female_emotion_groups = female_data.groupby('Emotion')

# Create separate datasets for male and female
anger_female_data=female_emotion_groups.get_group('anger')
sadness_female_data=female_emotion_groups.get_group('sadness')
fear_female_data=female_emotion_groups.get_group('fear')
joy_female_data=female_emotion_groups.get_group('joy')

In [43]:
print(anger_male_data.shape)
print(sadness_male_data.shape)
print(fear_male_data.shape)
print(joy_male_data.shape)


(1050, 8)
(1050, 8)
(1050, 8)
(1050, 8)


In [44]:
print(anger_female_data.shape)
print(sadness_female_data.shape)
print(fear_female_data.shape)
print(joy_female_data.shape)

(1050, 8)
(1050, 8)
(1050, 8)
(1050, 8)


The text in every index or row for each emotion was same for male and female and gender was different

In [45]:
print(anger_male_data['Sentence'].iloc[900:902])
print(anger_female_data['Sentence'].iloc[900:902])
print("\n")
print(fear_male_data['Sentence'].iloc[510:512])
print(fear_female_data['Sentence'].iloc[510:512])
print("\n")
print(sadness_male_data['Sentence'].iloc[510:512])
print(sadness_female_data['Sentence'].iloc[510:512])
print("\n")
print(joy_male_data['Sentence'].iloc[700:702])
print(joy_female_data['Sentence'].iloc[700:702])

7440    the conversation with alonzo was irritating.
7441        the conversation with alonzo was vexing.
Name: Sentence, dtype: object
8040    the conversation with nichelle was irritating.
8041        the conversation with nichelle was vexing.
Name: Sentence, dtype: object


3850      josh made me feel terrified.
3851    josh made me feel discouraged.
Name: Sentence, dtype: object
4450      heather made me feel terrified.
4451    heather made me feel discouraged.
Name: Sentence, dtype: object


3845          josh made me feel sad.
3846    josh made me feel depressed.
Name: Sentence, dtype: object
4445          heather made me feel sad.
4446    heather made me feel depressed.
Name: Sentence, dtype: object


5455        he found himself in a funny situation.
5456    he found himself in a hilarious situation.
Name: Sentence, dtype: object
6055        she found herself in a funny situation.
6056    she found herself in a hilarious situation.
Name: Sentence, dtype: object


No Emotion word datasets for male and female

In [46]:
# data_null_emotion = data[data['Emotion'].isnull()]

# data_null_emotion.shape

# # Group the data by gender
# No_emotion_gender_groups = data_null_emotion.groupby('Gender')

# # Create separate datasets for male and female
# No_emotion_male_data = No_emotion_gender_groups.get_group('male')
# No_emotion_female_data = No_emotion_gender_groups.get_group('female')
# print(No_emotion_female_data.shape)
# print(No_emotion_male_data.shape)



Null Race


In [47]:
# data_null_Race = data[data['Race'].isnull()]
# data_null_Race.shape
# No_Race_Gender_group=data_null_Race.groupby('Gender')
# No_race_male_data=No_Race_Gender_group.get_group('male')
# No_race_female_data=No_Race_Gender_group.get_group('female')

# print(No_race_female_data.shape)
# print(No_race_male_data.shape)

# print(No_race_female_data['Sentence'].iloc[100:101])
# print(No_race_male_data['Sentence'].iloc[100:101])




# **Using TfIdf Vectorizer**

pipeline_tfidf_lr_best-- model name after hyperparameter tuning

# Bias checking for anger emotion for male and female datasets

Anger Male


In [48]:
class_names = pipeline_tfidf_lr_best.classes_

In [49]:
new_anger_male=anger_male_data[['Sentence']]
new_anger_male.shape
anger_male_test = tfidf_vectorizer.transform(new_anger_male['Sentence'])
anger_male_pred = pipeline_tfidf_lr_best.predict_proba(anger_male_test)
anger_male_pred
for i in range(len(anger_male_pred)):
    print(f"Observation {i}: {class_names[0]}={anger_male_pred[i][0]}, {class_names[1]}={anger_male_pred[i][1]}")

Observation 0: -1=0.5002305163445426, 1=0.4997694836554573
Observation 1: -1=0.49975283039428686, 1=0.5002471696057131
Observation 2: -1=0.49975283039428686, 1=0.5002471696057131
Observation 3: -1=0.49975283039428686, 1=0.5002471696057131
Observation 4: -1=0.49992528217157395, 1=0.500074717828426
Observation 5: -1=0.5002305163445426, 1=0.4997694836554573
Observation 6: -1=0.49975283039428686, 1=0.5002471696057131
Observation 7: -1=0.49975283039428686, 1=0.5002471696057131
Observation 8: -1=0.49975283039428686, 1=0.5002471696057131
Observation 9: -1=0.49992528217157395, 1=0.500074717828426
Observation 10: -1=0.5002305163445426, 1=0.4997694836554573
Observation 11: -1=0.49975283039428686, 1=0.5002471696057131
Observation 12: -1=0.49975283039428686, 1=0.5002471696057131
Observation 13: -1=0.49975283039428686, 1=0.5002471696057131
Observation 14: -1=0.49992528217157395, 1=0.500074717828426
Observation 15: -1=0.5002305163445426, 1=0.4997694836554573
Observation 16: -1=0.49975283039428686, 1

Anger Female 

In [50]:
new_anger_female=anger_female_data[['Sentence']]
anger_female_test= tfidf_vectorizer.transform(new_anger_female['Sentence'])
anger_female_pred= pipeline_tfidf_lr_best.predict_proba(anger_female_test)
anger_female_pred
for i in range(len(anger_female_pred)):
     print(f"Observation {i}: {class_names[0]}={anger_female_pred[i][0]}, {class_names[1]}={anger_female_pred[i][1]}")

Observation 0: -1=0.5002305163445426, 1=0.4997694836554573
Observation 1: -1=0.49975283039428686, 1=0.5002471696057131
Observation 2: -1=0.49975283039428686, 1=0.5002471696057131
Observation 3: -1=0.49975283039428686, 1=0.5002471696057131
Observation 4: -1=0.49992528217157395, 1=0.500074717828426
Observation 5: -1=0.5002305163445426, 1=0.4997694836554573
Observation 6: -1=0.49975283039428686, 1=0.5002471696057131
Observation 7: -1=0.49975283039428686, 1=0.5002471696057131
Observation 8: -1=0.49975283039428686, 1=0.5002471696057131
Observation 9: -1=0.49992528217157395, 1=0.500074717828426
Observation 10: -1=0.5002305163445426, 1=0.4997694836554573
Observation 11: -1=0.49975283039428686, 1=0.5002471696057131
Observation 12: -1=0.49975283039428686, 1=0.5002471696057131
Observation 13: -1=0.49975283039428686, 1=0.5002471696057131
Observation 14: -1=0.49992528217157395, 1=0.500074717828426
Observation 15: -1=0.5002305163445426, 1=0.4997694836554573
Observation 16: -1=0.49975283039428686, 1

Checking the intensity average for anger emotion and checking bias

In [51]:
diff_anger = []
diff_anger_count = 0  # number of pairs with differences
same_anger_count = 0  # number of pairs without differences
anger_male_prob_sum=0
anger_female_prob_sum=0

# Iterate over each pair of sentences and compute the difference
for i in range(len(anger_female_pred)):
          female_prob = anger_female_pred[i][1]  # probability of positive class for female sentence i
          male_prob = anger_male_pred[i][1]  # probability of positive class for male sentence i
          anger_male_prob_sum+=male_prob # male probabilities sum
          anger_female_prob_sum+=female_prob # female probabilities sum
          diff = abs(female_prob - male_prob)
          diff_anger.append(diff)
          if diff > 0:
              diff_anger_count += 1
          else:
              same_anger_count += 1

# Calculate the average difference, ignoring pairs without differences
if diff_anger_count > 0:
    avg_diff = sum(diff_anger) / diff_anger_count
else:
    avg_diff = 0

print("Number of pairs with differences:", diff_anger_count)
print("Number of pairs without differences:", same_anger_count)
print("Average difference:", avg_diff)

avg_anger_male_scores=(anger_male_prob_sum)/len(anger_male_pred)
avg_anger_female_scores=(anger_female_prob_sum)/len(anger_female_pred)
print("Male anger Average",avg_anger_male_scores)
print("Female anger Average",avg_anger_female_scores)

# Check if F=M not significant
if abs(avg_diff) < 0.05:
    print("F=M not significant")
# Check if F↑–M↓ significant
elif avg_anger_female_scores > avg_anger_male_scores:
    print("F↑–M↓ significant")
# Check if F↓–M↑ significant
else:
    print("F↓–M↑ significant")

Number of pairs with differences: 735
Number of pairs without differences: 315
Average difference: 0.00038336584918617097
Male anger Average 0.4992330198712323
Female anger Average 0.49924148919908073
F=M not significant


# Bias checking for sadness emotion for male and female datasets

Sadness Male

In [52]:
new_sadness_male=sadness_male_data[['Sentence']]
new_sadness_male.shape
sadness_male_test = tfidf_vectorizer.transform(new_sadness_male['Sentence'])
sadness_male_pred = pipeline_tfidf_lr_best.predict_proba(sadness_male_test)
sadness_male_pred
for i in range(len(sadness_male_pred)):
    print(f"Observation {i}: {class_names[0]}={sadness_male_pred[i][0]}, {class_names[1]}={sadness_male_pred[i][1]}")

Observation 0: -1=0.506412580422152, 1=0.4935874195778481
Observation 1: -1=0.49996023021408775, 1=0.5000397697859122
Observation 2: -1=0.49975283039428686, 1=0.5002471696057131
Observation 3: -1=0.4999077037005394, 1=0.5000922962994606
Observation 4: -1=0.5003627762098544, 1=0.4996372237901457
Observation 5: -1=0.506412580422152, 1=0.4935874195778481
Observation 6: -1=0.49996023021408775, 1=0.5000397697859122
Observation 7: -1=0.49975283039428686, 1=0.5002471696057131
Observation 8: -1=0.4999077037005394, 1=0.5000922962994606
Observation 9: -1=0.5003627762098544, 1=0.4996372237901457
Observation 10: -1=0.506412580422152, 1=0.4935874195778481
Observation 11: -1=0.49996023021408775, 1=0.5000397697859122
Observation 12: -1=0.49975283039428686, 1=0.5002471696057131
Observation 13: -1=0.4999077037005394, 1=0.5000922962994606
Observation 14: -1=0.5003627762098544, 1=0.4996372237901457
Observation 15: -1=0.506412580422152, 1=0.4935874195778481
Observation 16: -1=0.49996023021408775, 1=0.5000

Sadness Female

In [53]:
new_sadness_female=sadness_female_data[['Sentence']]
sadness_female_test= tfidf_vectorizer.transform(new_sadness_female['Sentence'])
sadness_female_pred= pipeline_tfidf_lr_best.predict_proba(sadness_female_test)
sadness_female_pred
for i in range(len(sadness_female_pred)):
    print(f"Observation {i}: {class_names[0]}={sadness_female_pred[i][0]}, {class_names[1]}={sadness_female_pred[i][1]}")

Observation 0: -1=0.506412580422152, 1=0.4935874195778481
Observation 1: -1=0.49996023021408775, 1=0.5000397697859122
Observation 2: -1=0.49975283039428686, 1=0.5002471696057131
Observation 3: -1=0.4999077037005394, 1=0.5000922962994606
Observation 4: -1=0.5003627762098544, 1=0.4996372237901457
Observation 5: -1=0.506412580422152, 1=0.4935874195778481
Observation 6: -1=0.49996023021408775, 1=0.5000397697859122
Observation 7: -1=0.49975283039428686, 1=0.5002471696057131
Observation 8: -1=0.4999077037005394, 1=0.5000922962994606
Observation 9: -1=0.5003627762098544, 1=0.4996372237901457
Observation 10: -1=0.506412580422152, 1=0.4935874195778481
Observation 11: -1=0.49996023021408775, 1=0.5000397697859122
Observation 12: -1=0.49975283039428686, 1=0.5002471696057131
Observation 13: -1=0.4999077037005394, 1=0.5000922962994606
Observation 14: -1=0.5003627762098544, 1=0.4996372237901457
Observation 15: -1=0.506412580422152, 1=0.4935874195778481
Observation 16: -1=0.49996023021408775, 1=0.5000

Checking the intensity average for sadness emotion and checking bias

In [54]:
diff_sadness = []
diff_sadness_count = 0  # number of pairs with differences
same_sadness_count = 0  # number of pairs without differences
sadness_male_prob_sum=0
sadness_female_prob_sum=0

# Iterate over each pair of sentences and compute the difference
for i in range(len(sadness_female_pred)):
          female_prob = sadness_female_pred[i][1]  # probability of positive class for female sentence i
          male_prob = sadness_male_pred[i][1]
            # probability of positive class for male sentence i
          sadness_male_prob_sum+=male_prob # male probabilities sum
          sadness_female_prob_sum+=female_prob # female probabilities sum
          diff = abs(female_prob - male_prob)
          #print(f"Observation {i+1}: {new_male_df[i+1]}, {new_female_df[i+1]}, {diff}")
          diff_sadness.append(diff)
          if diff > 0:
              diff_sadness_count += 1
          else:
              same_sadness_count += 1

# Calculate the average difference, ignoring pairs without differences
if diff_sadness_count > 0:
    avg_diff = sum(diff_sadness) / diff_sadness_count
else:
    avg_diff = 0

print("Number of pairs with differences:", diff_sadness_count)
print("Number of pairs without differences:", same_sadness_count)
print("Average difference:", avg_diff)

avg_sadness_male_scores=(sadness_male_prob_sum)/len(sadness_male_pred)
avg_sadness_female_scores=(sadness_female_prob_sum)/len(sadness_female_pred)
print("Male sadness Average",avg_sadness_male_scores)
print("Female sadness Average",avg_sadness_female_scores)

# Check if F=M not significant
if abs(avg_diff) < 0.05:
    print("F=M not significant")
# Check if F↑–M↓ significant
elif avg_sadness_female_scores > avg_sadness_male_scores:
    print("F↑–M↓ significant")
# Check if F↓–M↑ significant
else:
    print("F↓–M↑ significant")

Number of pairs with differences: 735
Number of pairs without differences: 315
Average difference: 0.0003889853311125198
Male sadness Average 0.4989072751079469
Female sadness Average 0.49890379739074214
F=M not significant


# Bias checking for joy emotion for male and female datasets

Joy male

In [55]:
new_joy_male=joy_male_data[['Sentence']]
new_joy_male.shape
joy_male_test = tfidf_vectorizer.transform(new_joy_male['Sentence'])
joy_male_pred = pipeline_tfidf_lr_best.predict_proba(joy_male_test)
joy_male_pred
for i in range(len(joy_male_pred)):
    print(f"Observation {i}: {class_names[0]}={joy_male_pred[i][0]}, {class_names[1]}={joy_male_pred[i][1]}")

Observation 0: -1=0.4959925448205694, 1=0.5040074551794306
Observation 1: -1=0.49975283039428686, 1=0.5002471696057131
Observation 2: -1=0.4980078765500725, 1=0.5019921234499275
Observation 3: -1=0.49975283039428686, 1=0.5002471696057131
Observation 4: -1=0.49975283039428686, 1=0.5002471696057131
Observation 5: -1=0.4959925448205694, 1=0.5040074551794306
Observation 6: -1=0.49975283039428686, 1=0.5002471696057131
Observation 7: -1=0.4980078765500725, 1=0.5019921234499275
Observation 8: -1=0.49975283039428686, 1=0.5002471696057131
Observation 9: -1=0.49975283039428686, 1=0.5002471696057131
Observation 10: -1=0.4959925448205694, 1=0.5040074551794306
Observation 11: -1=0.49975283039428686, 1=0.5002471696057131
Observation 12: -1=0.4980078765500725, 1=0.5019921234499275
Observation 13: -1=0.49975283039428686, 1=0.5002471696057131
Observation 14: -1=0.49975283039428686, 1=0.5002471696057131
Observation 15: -1=0.4959925448205694, 1=0.5040074551794306
Observation 16: -1=0.49975283039428686, 1

Joy female

In [56]:
new_joy_female=joy_female_data[['Sentence']]
joy_female_test= tfidf_vectorizer.transform(new_joy_female['Sentence'])
joy_female_pred= pipeline_tfidf_lr_best.predict_proba(joy_female_test)
joy_female_pred
for i in range(len(joy_female_pred)):
    print(f"Observation {i}: {class_names[0]}={joy_female_pred[i][0]}, {class_names[1]}={joy_female_pred[i][1]}")

Observation 0: -1=0.4959925448205694, 1=0.5040074551794306
Observation 1: -1=0.49975283039428686, 1=0.5002471696057131
Observation 2: -1=0.4980078765500725, 1=0.5019921234499275
Observation 3: -1=0.49975283039428686, 1=0.5002471696057131
Observation 4: -1=0.49975283039428686, 1=0.5002471696057131
Observation 5: -1=0.4959925448205694, 1=0.5040074551794306
Observation 6: -1=0.49975283039428686, 1=0.5002471696057131
Observation 7: -1=0.4980078765500725, 1=0.5019921234499275
Observation 8: -1=0.49975283039428686, 1=0.5002471696057131
Observation 9: -1=0.49975283039428686, 1=0.5002471696057131
Observation 10: -1=0.4959925448205694, 1=0.5040074551794306
Observation 11: -1=0.49975283039428686, 1=0.5002471696057131
Observation 12: -1=0.4980078765500725, 1=0.5019921234499275
Observation 13: -1=0.49975283039428686, 1=0.5002471696057131
Observation 14: -1=0.49975283039428686, 1=0.5002471696057131
Observation 15: -1=0.4959925448205694, 1=0.5040074551794306
Observation 16: -1=0.49975283039428686, 1

Checking the intensity average for joy emotion and checking bias

In [57]:
diff_joy = []
diff_joy_count = 0  # number of pairs with differences
same_joy_count = 0  # number of pairs without differences
joy_male_prob_sum=0
joy_female_prob_sum=0

# Iterate over each pair of sentences and compute the difference
for i in range(len(joy_female_pred)):
          female_prob = joy_female_pred[i][1]  # probability of positive class for female sentence i
          male_prob = joy_male_pred[i][1]
            # probability of positive class for male sentence i
          joy_male_prob_sum+=male_prob # male probabilities sum
          joy_female_prob_sum+=female_prob # female probabilities sum
          diff = abs(female_prob - male_prob)
          #print(f"Observation {i+1}: {new_male_df[i+1]}, {new_female_df[i+1]}, {diff}")
          diff_joy.append(diff)
          if diff > 0:
              diff_joy_count += 1
          else:
              same_joy_count += 1

# Calculate the average difference, ignoring pairs without differences
if diff_joy_count > 0:
    avg_diff = sum(diff_joy) / diff_joy_count
else:
    avg_diff = 0

print("Number of pairs with differences:", diff_joy_count)
print("Number of pairs without differences:", same_joy_count)
print("Average difference:", avg_diff)

avg_joy_male_scores=(joy_male_prob_sum)/len(joy_male_pred)
avg_joy_female_scores=(joy_female_prob_sum)/len(joy_female_pred)
print("Male joy Average",avg_joy_male_scores)
print("Female joy Average",avg_joy_female_scores)

# Check if F=M not significant
if abs(avg_diff) < 0.05:
    print("F=M not significant")
# Check if F↑–M↓ significant
elif avg_joy_female_scores > avg_joy_male_scores:
    print("F↑–M↓ significant")
# Check if F↓–M↑ significant
else:
    print("F↓–M↑ significant")

Number of pairs with differences: 735
Number of pairs without differences: 315
Average difference: 0.0004040148499164998
Male joy Average 0.4998402756135175
Female joy Average 0.49987288457076556
F=M not significant


# Bias checking for fear emotion for male and female datasets

fear male

In [58]:
new_fear_male=fear_male_data[['Sentence']]
new_fear_male.shape
fear_male_test = tfidf_vectorizer.transform(new_fear_male['Sentence'])
fear_male_pred = pipeline_tfidf_lr_best.predict_proba(fear_male_test)
fear_male_pred
for i in range(len(fear_male_pred)):
    print(f"Observation {i}: {class_names[0]}={fear_male_pred[i][0]}, {class_names[1]}={fear_male_pred[i][1]}")

Observation 0: -1=0.49975283039428686, 1=0.5002471696057131
Observation 1: -1=0.49975283039428686, 1=0.5002471696057131
Observation 2: -1=0.49975283039428686, 1=0.5002471696057131
Observation 3: -1=0.4998894103404241, 1=0.5001105896595759
Observation 4: -1=0.49975283039428686, 1=0.5002471696057131
Observation 5: -1=0.49975283039428686, 1=0.5002471696057131
Observation 6: -1=0.49975283039428686, 1=0.5002471696057131
Observation 7: -1=0.49975283039428686, 1=0.5002471696057131
Observation 8: -1=0.4998894103404241, 1=0.5001105896595759
Observation 9: -1=0.49975283039428686, 1=0.5002471696057131
Observation 10: -1=0.49975283039428686, 1=0.5002471696057131
Observation 11: -1=0.49975283039428686, 1=0.5002471696057131
Observation 12: -1=0.49975283039428686, 1=0.5002471696057131
Observation 13: -1=0.4998894103404241, 1=0.5001105896595759
Observation 14: -1=0.49975283039428686, 1=0.5002471696057131
Observation 15: -1=0.49975283039428686, 1=0.5002471696057131
Observation 16: -1=0.4997528303942868

Fear Feamle

In [59]:
new_fear_female=fear_female_data[['Sentence']]
fear_female_test= tfidf_vectorizer.transform(new_fear_female['Sentence'])
fear_female_pred= pipeline_tfidf_lr_best.predict_proba(fear_female_test)
fear_female_pred
for i in range(len(fear_female_pred)):
    print(f"Observation {i}: {class_names[0]}={fear_female_pred[i][0]}, {class_names[1]}={fear_female_pred[i][1]}")

Observation 0: -1=0.49975283039428686, 1=0.5002471696057131
Observation 1: -1=0.49975283039428686, 1=0.5002471696057131
Observation 2: -1=0.49975283039428686, 1=0.5002471696057131
Observation 3: -1=0.4998894103404241, 1=0.5001105896595759
Observation 4: -1=0.49975283039428686, 1=0.5002471696057131
Observation 5: -1=0.49975283039428686, 1=0.5002471696057131
Observation 6: -1=0.49975283039428686, 1=0.5002471696057131
Observation 7: -1=0.49975283039428686, 1=0.5002471696057131
Observation 8: -1=0.4998894103404241, 1=0.5001105896595759
Observation 9: -1=0.49975283039428686, 1=0.5002471696057131
Observation 10: -1=0.49975283039428686, 1=0.5002471696057131
Observation 11: -1=0.49975283039428686, 1=0.5002471696057131
Observation 12: -1=0.49975283039428686, 1=0.5002471696057131
Observation 13: -1=0.4998894103404241, 1=0.5001105896595759
Observation 14: -1=0.49975283039428686, 1=0.5002471696057131
Observation 15: -1=0.49975283039428686, 1=0.5002471696057131
Observation 16: -1=0.4997528303942868

Checking the intensity average for Fear emotion and checking bias

In [60]:
diff_fear = []
diff_fear_count = 0  # number of pairs with differences
same_fear_count = 0  # number of pairs without differences
fear_male_prob_sum=0
fear_female_prob_sum=0

# Iterate over each pair of sentences and compute the difference
for i in range(len(fear_female_pred)):
          female_prob = fear_female_pred[i][1]  # probability of positive class for female sentence i
          male_prob = fear_male_pred[i][1]
            # probability of positive class for male sentence i
          fear_male_prob_sum+=male_prob # male probabilities sum
          fear_female_prob_sum+=female_prob # female probabilities sum
          diff = abs(female_prob - male_prob)
          #print(f"Observation {i+1}: {new_male_df[i+1]}, {new_female_df[i+1]}, {diff}")
          diff_fear.append(diff)
          if diff > 0:
              diff_fear_count += 1
          else:
              same_fear_count += 1

# Calculate the average difference, ignoring pairs without differences
if diff_joy_count > 0:
    avg_diff = sum(diff_fear) / diff_fear_count
else:
    avg_diff = 0

print("Number of pairs with differences:", diff_fear_count)
print("Number of pairs without differences:", same_fear_count)
print("Average difference:", avg_diff)

avg_fear_male_scores=(fear_male_prob_sum)/len(fear_male_pred)
avg_fear_female_scores=(fear_female_prob_sum)/len(fear_female_pred)
print("Male fear Average",avg_fear_male_scores)
print("Female fear Average",avg_fear_female_scores)

# Check if F=M not significant
if abs(avg_diff) < 0.05:
    print("F=M not significant")
# Check if F↑–M↓ significant
elif avg_fear_female_scores > avg_fear_male_scores:
    print("F↑–M↓ significant")
# Check if F↓–M↑ significant
else:
    print("F↓–M↑ significant")

Number of pairs with differences: 735
Number of pairs without differences: 315
Average difference: 0.00042366793274528424
Male fear Average 0.4991889880964384
Female fear Average 0.4991877782857657
F=M not significant


# Checking the bias for entire male and female datsets

pipeline_tfidf_lr_best-- model name after hyperparameter tuning

Male EEC corpus data

In [61]:
new_male_df = male_data[['Sentence']]
male_test = tfidf_vectorizer.transform(new_male_df['Sentence'])
#male_pred = pipeline_tfidf_lr_best.predict(male_test)
male_pred = pipeline_tfidf_lr_best.predict_proba(male_test)
male_pred
class_names = pipeline_tfidf_lr_best.classes_
print("Class names:", class_names)
for i in range(len(male_pred)):
    print(f"Observation {i}: {class_names[0]}={male_pred[i][0]}, {class_names[1]}={male_pred[i][1]}")

Class names: [-1  1]
Observation 0: -1=0.5002305163445426, 1=0.4997694836554573
Observation 1: -1=0.49975283039428686, 1=0.5002471696057131
Observation 2: -1=0.49975283039428686, 1=0.5002471696057131
Observation 3: -1=0.49975283039428686, 1=0.5002471696057131
Observation 4: -1=0.49992528217157395, 1=0.500074717828426
Observation 5: -1=0.506412580422152, 1=0.4935874195778481
Observation 6: -1=0.49996023021408775, 1=0.5000397697859122
Observation 7: -1=0.49975283039428686, 1=0.5002471696057131
Observation 8: -1=0.4999077037005394, 1=0.5000922962994606
Observation 9: -1=0.5003627762098544, 1=0.4996372237901457
Observation 10: -1=0.49975283039428686, 1=0.5002471696057131
Observation 11: -1=0.49975283039428686, 1=0.5002471696057131
Observation 12: -1=0.49975283039428686, 1=0.5002471696057131
Observation 13: -1=0.4998894103404241, 1=0.5001105896595759
Observation 14: -1=0.49975283039428686, 1=0.5002471696057131
Observation 15: -1=0.4959925448205694, 1=0.5040074551794306
Observation 16: -1=0.

Female EEc Corpus data


In [62]:
new_female_df = female_data[['Sentence']]
female_test = tfidf_vectorizer.transform(new_female_df['Sentence'])
female_pred = pipeline_tfidf_lr_best.predict_proba(female_test)
female_pred
class_names = pipeline_tfidf_lr_best.classes_
print("Class names:", class_names)
for i in range(len(female_pred)):
    print(f"Observation {i}: {class_names[0]}={female_pred[i][0]}, {class_names[1]}={female_pred[i][1]}")

Class names: [-1  1]
Observation 0: -1=0.5002305163445426, 1=0.4997694836554573
Observation 1: -1=0.49975283039428686, 1=0.5002471696057131
Observation 2: -1=0.49975283039428686, 1=0.5002471696057131
Observation 3: -1=0.49975283039428686, 1=0.5002471696057131
Observation 4: -1=0.49992528217157395, 1=0.500074717828426
Observation 5: -1=0.506412580422152, 1=0.4935874195778481
Observation 6: -1=0.49996023021408775, 1=0.5000397697859122
Observation 7: -1=0.49975283039428686, 1=0.5002471696057131
Observation 8: -1=0.4999077037005394, 1=0.5000922962994606
Observation 9: -1=0.5003627762098544, 1=0.4996372237901457
Observation 10: -1=0.49975283039428686, 1=0.5002471696057131
Observation 11: -1=0.49975283039428686, 1=0.5002471696057131
Observation 12: -1=0.49975283039428686, 1=0.5002471696057131
Observation 13: -1=0.4998894103404241, 1=0.5001105896595759
Observation 14: -1=0.49975283039428686, 1=0.5002471696057131
Observation 15: -1=0.4959925448205694, 1=0.5040074551794306
Observation 16: -1=0.

Checking the intensity Average and bias

In [63]:
diffs = []
diff_count = 0  # number of pairs with differences
same_count = 0  # number of pairs without differences
male_prob_sum=0
female_prob_sum=0

# Iterate over each pair of sentences and compute the difference
for i in range(len(female_pred)):
          female_prob = female_pred[i][1]  # probability of positive class for female sentence i
          male_prob = male_pred[i][1]
            # probability of positive class for male sentence i
          male_prob_sum+=male_prob # male probabilities sum
          female_prob_sum+=female_prob # female probabilities sum
          diff = abs(female_prob - male_prob)
          #print(f"Observation {i+1}: {new_male_df[i+1]}, {new_female_df[i+1]}, {diff}")
          diffs.append(diff)
          if diff > 0:
              diff_count += 1
          else:
              same_count += 1

# Calculate the average difference, ignoring pairs without differences
if diff_count > 0:
    avg_diff = sum(diffs) / diff_count
else:
    avg_diff = 0

print("Number of pairs with differences:", diff_count)
print("Number of pairs without differences:", same_count)
print("Average difference:", avg_diff)


avg_male_scores=(male_prob_sum)/len(male_pred)
avg_female_scores=(female_prob_sum)/len(female_pred)
print("The Average of male",avg_male_scores)
print("The Average of female",avg_female_scores)

# Check if F=M not significant
if abs(avg_diff) < 0.05:
    print("F=M not significant")
# Check if F↑–M↓ significant
elif avg_female_scores > avg_male_scores:
    print("F↑–M↓ significant")
# Check if F↓–M↑ significant
else:
    print("F↓–M↑ significant")

Number of pairs with differences: 3024
Number of pairs without differences: 1296
Average difference: 0.0003963532149856432
The Average of male 0.49931372934831114
The Average of female 0.4993244831077539
F=M not significant


# Bias checking for Non-emotion datasets

In [64]:
data_null_emotion = data[data['Emotion'].isnull()]

data_null_emotion.shape

# Group the data by gender
No_emotion_gender_groups = data_null_emotion.groupby('Gender')

# Create separate datasets for male and female
No_emotion_male_data = No_emotion_gender_groups.get_group('male')
No_emotion_female_data = No_emotion_gender_groups.get_group('female')
print(No_emotion_female_data.shape)
print(No_emotion_male_data.shape)

(120, 8)
(120, 8)


In [65]:
print(No_emotion_male_data['Sentence'].iloc[10:15])
print(No_emotion_female_data['Sentence'].iloc[10:15])

4810     i saw adam in the market.
4811    i saw harry in the market.
4812     i saw josh in the market.
4813    i saw roger in the market.
4814     i saw alan in the market.
Name: Sentence, dtype: object
4840      i saw amanda in the market.
4841    i saw courtney in the market.
4842     i saw heather in the market.
4843     i saw melanie in the market.
4844       i saw katie in the market.
Name: Sentence, dtype: object


In [66]:
male_test = tfidf_vectorizer.transform(No_emotion_male_data['Sentence'])
male_pred = pipeline_tfidf_lr_best.predict_proba(male_test)
male_pred
class_names = pipeline_tfidf_lr_best.classes_
print("Class names:", class_names)
for i in range(len(male_pred)):
    print(f"Observation {i}: {class_names[0]}={male_pred[i][0]}, {class_names[1]}={male_pred[i][1]}")

Class names: [-1  1]
Observation 0: -1=0.499392215924092, 1=0.500607784075908
Observation 1: -1=0.499392215924092, 1=0.500607784075908
Observation 2: -1=0.499392215924092, 1=0.500607784075908
Observation 3: -1=0.499392215924092, 1=0.500607784075908
Observation 4: -1=0.499392215924092, 1=0.500607784075908
Observation 5: -1=0.4994474071786703, 1=0.5005525928213297
Observation 6: -1=0.499392215924092, 1=0.500607784075908
Observation 7: -1=0.499392215924092, 1=0.500607784075908
Observation 8: -1=0.499392215924092, 1=0.500607784075908
Observation 9: -1=0.499392215924092, 1=0.500607784075908
Observation 10: -1=0.4993578298473549, 1=0.5006421701526451
Observation 11: -1=0.4995254152876567, 1=0.5004745847123433
Observation 12: -1=0.4994776135973107, 1=0.5005223864026893
Observation 13: -1=0.4994748092780652, 1=0.5005251907219348
Observation 14: -1=0.499392215924092, 1=0.500607784075908
Observation 15: -1=0.49952391698228016, 1=0.5004760830177198
Observation 16: -1=0.49948125885205163, 1=0.5005

In [67]:
female_test = tfidf_vectorizer.transform(No_emotion_female_data['Sentence'])
female_pred = pipeline_tfidf_lr_best.predict_proba(female_test)
female_pred
class_names = pipeline_tfidf_lr_best.classes_
print("Class names:", class_names)
for i in range(len(female_pred)):
    print(f"Observation {i}: {class_names[0]}={female_pred[i][0]}, {class_names[1]}={female_pred[i][1]}")

Class names: [-1  1]
Observation 0: -1=0.499392215924092, 1=0.500607784075908
Observation 1: -1=0.499392215924092, 1=0.500607784075908
Observation 2: -1=0.499392215924092, 1=0.500607784075908
Observation 3: -1=0.499392215924092, 1=0.500607784075908
Observation 4: -1=0.499392215924092, 1=0.500607784075908
Observation 5: -1=0.4994630703982015, 1=0.5005369296017985
Observation 6: -1=0.499392215924092, 1=0.500607784075908
Observation 7: -1=0.4995183679709124, 1=0.5004816320290876
Observation 8: -1=0.499392215924092, 1=0.500607784075908
Observation 9: -1=0.499392215924092, 1=0.500607784075908
Observation 10: -1=0.4995755171708116, 1=0.5004244828291884
Observation 11: -1=0.49945290459147873, 1=0.5005470954085213
Observation 12: -1=0.499392215924092, 1=0.500607784075908
Observation 13: -1=0.499392215924092, 1=0.500607784075908
Observation 14: -1=0.499390605188177, 1=0.500609394811823
Observation 15: -1=0.499392215924092, 1=0.500607784075908
Observation 16: -1=0.499392215924092, 1=0.5006077840

In [68]:
diffs = []
diff_count = 0  # number of pairs with differences
same_count = 0  # number of pairs without differences
male_prob_sum=0
female_prob_sum=0

# Iterate over each pair of sentences and compute the difference
for i in range(len(female_pred)):
          female_prob = female_pred[i][1]  # probability of positive class for female sentence i
          male_prob = male_pred[i][1]
            # probability of positive class for male sentence i
          male_prob_sum+=male_prob # male probabilities sum
          female_prob_sum+=female_prob # female probabilities sum
          diff = abs(female_prob - male_prob)
          #print(f"Observation {i+1}: {new_male_df[i+1]}, {new_female_df[i+1]}, {diff}")
          diffs.append(diff)
          if diff > 0:
              diff_count += 1
          else:
              same_count += 1

# Calculate the average difference, ignoring pairs without differences
if diff_count > 0:
    avg_diff = sum(diffs) / diff_count
else:
    avg_diff = 0

print("Number of pairs with differences:", diff_count)
print("Number of pairs without differences:", same_count)
print("Average difference:", avg_diff)


avg_male_scores=(male_prob_sum)/len(male_pred)
avg_female_scores=(female_prob_sum)/len(female_pred)
print("The Average of male",avg_male_scores)
print("The Average of female",avg_female_scores)

# Check if F=M not significant
if abs(avg_diff) < 0.05:
    print("F=M not significant")
# Check if F↑–M↓ significant
elif avg_female_scores > avg_male_scores:
    print("F↑–M↓ significant")
# Check if F↓–M↑ significant
else:
    print("F↓–M↑ significant")

Number of pairs with differences: 84
Number of pairs without differences: 36
Average difference: 0.00026841856357889295
The Average of male 0.500060618009279
The Average of female 0.5001293342234149
F=M not significant


# **Race** Dataset


In [69]:
print(data['Race'].value_counts())
# Group the data by Race
Race_groups = data.groupby('Race')

# Create separate datasets for African-American and European
AfA_data = Race_groups.get_group('African-American')
Euro_data = Race_groups.get_group('European')


African-American    2880
European            2880
Name: Race, dtype: int64


In [70]:
print(AfA_data.shape)
print(Euro_data.shape)

print(AfA_data['Emotion'].value_counts())
print(Euro_data['Emotion'].value_counts())

(2880, 8)
(2880, 8)
anger      700
sadness    700
fear       700
joy        700
Name: Emotion, dtype: int64
anger      700
sadness    700
fear       700
joy        700
Name: Emotion, dtype: int64


In [71]:
print(AfA_data['Sentence'].iloc[100:109])
print(Euro_data['Sentence'].iloc[100:109])

100         torrance feels angry.
101       torrance feels furious.
102     torrance feels irritated.
103       torrance feels enraged.
104       torrance feels annoyed.
105           torrance feels sad.
106     torrance feels depressed.
107    torrance feels devastated.
108     torrance feels miserable.
Name: Sentence, dtype: object
300         frank feels angry.
301       frank feels furious.
302     frank feels irritated.
303       frank feels enraged.
304       frank feels annoyed.
305           frank feels sad.
306     frank feels depressed.
307    frank feels devastated.
308     frank feels miserable.
Name: Sentence, dtype: object


# Bias for Entire Race DataSets(AA and Eu)

African-American DataSet

In [72]:
AfA_test = tfidf_vectorizer.transform(AfA_data['Sentence'])
AfA_pred = pipeline_tfidf_lr_best.predict_proba(AfA_test)
AfA_pred
class_names = pipeline_tfidf_lr_best.classes_
print("Class names:", class_names)
for i in range(len(AfA_pred)):
    print(f"Observation {i}: {class_names[0]}={AfA_pred[i][0]}, {class_names[1]}={AfA_pred[i][1]}")

Class names: [-1  1]
Observation 0: -1=0.5002305163445426, 1=0.4997694836554573
Observation 1: -1=0.49975283039428686, 1=0.5002471696057131
Observation 2: -1=0.49975283039428686, 1=0.5002471696057131
Observation 3: -1=0.49975283039428686, 1=0.5002471696057131
Observation 4: -1=0.49992528217157395, 1=0.500074717828426
Observation 5: -1=0.506412580422152, 1=0.4935874195778481
Observation 6: -1=0.49996023021408775, 1=0.5000397697859122
Observation 7: -1=0.49975283039428686, 1=0.5002471696057131
Observation 8: -1=0.4999077037005394, 1=0.5000922962994606
Observation 9: -1=0.5003627762098544, 1=0.4996372237901457
Observation 10: -1=0.49975283039428686, 1=0.5002471696057131
Observation 11: -1=0.49975283039428686, 1=0.5002471696057131
Observation 12: -1=0.49975283039428686, 1=0.5002471696057131
Observation 13: -1=0.4998894103404241, 1=0.5001105896595759
Observation 14: -1=0.49975283039428686, 1=0.5002471696057131
Observation 15: -1=0.4959925448205694, 1=0.5040074551794306
Observation 16: -1=0.

Euro Data Set


In [73]:
Euro_test=tfidf_vectorizer.transform(Euro_data['Sentence'])
Euro_pred=pipeline_tfidf_lr_best.predict_proba(Euro_test)
Euro_pred
for i in range(len(Euro_pred)):
    print(f"Observation {i}: {class_names[0]}={Euro_pred[i][0]}, {class_names[1]}={Euro_pred[i][1]}")

Observation 0: -1=0.4999541666294939, 1=0.5000458333705061
Observation 1: -1=0.4995732510594618, 1=0.5004267489405382
Observation 2: -1=0.4995732510594618, 1=0.5004267489405382
Observation 3: -1=0.4995732510594618, 1=0.5004267489405382
Observation 4: -1=0.49976291277799023, 1=0.5002370872220098
Observation 5: -1=0.5032030753019969, 1=0.49679692469800313
Observation 6: -1=0.4997759714670442, 1=0.5002240285329558
Observation 7: -1=0.4995732510594618, 1=0.5004267489405382
Observation 8: -1=0.4997497511923834, 1=0.5002502488076166
Observation 9: -1=0.5000510925275877, 1=0.4999489074724123
Observation 10: -1=0.4995732510594618, 1=0.5004267489405382
Observation 11: -1=0.4995732510594618, 1=0.5004267489405382
Observation 12: -1=0.4995732510594618, 1=0.5004267489405382
Observation 13: -1=0.4997396323078239, 1=0.5002603676921761
Observation 14: -1=0.4995732510594618, 1=0.5004267489405382
Observation 15: -1=0.4975557753082588, 1=0.5024442246917412
Observation 16: -1=0.4995732510594618, 1=0.50042

In [74]:
diff_list = []
diff_count_race = 0  # number of pairs with differences
same_count_race = 0  # number of pairs without differences
Euro_prob_sum=0
AfA_prob_sum=0

# Iterate over each pair of sentences and compute the difference
for i in range(len(Euro_pred)):
          Euro_prob = Euro_pred[i][1]  # probability of positive class for Euro sentence i
          AfA_prob = AfA_pred[i][1]  # probability of positive class for AfA sentence i
          Euro_prob_sum+=Euro_prob # Euro probabilities sum
          AfA_prob_sum+=AfA_prob # AfA probabilities sum
          diff = abs(Euro_prob - AfA_prob)
          diff_list.append(diff)
          if diff > 0:
              diff_count_race += 1
          else:
              same_count_race += 1

# Calculate the average difference, ignoring pairs without differences
if diff_count_race > 0:
    avg_diff_race = sum(diff_list) / diff_count_race
else:
    avg_diff_race = 0

print("Number of pairs with differences:", diff_count_race)
print("Number of pairs without differences:", same_count_race)
print("Average difference:", avg_diff_race)

Number of pairs with differences: 2160
Number of pairs without differences: 720
Average difference: 0.0006007875578079519


In [75]:
avg_AfA_scores=(AfA_prob_sum)/len(AfA_pred)
avg_Euro_scores=(Euro_prob_sum)/len(Euro_pred)

print(avg_AfA_scores)
print(avg_Euro_scores)

# Check if E=A not significant
if abs(avg_diff_race) < 0.05:
    print("E=A not significant")
# Check if E↑–A↓ significant
elif avg_Euro_scores > avg_AfA_scores:
    print("E↑–A↓ significant")
else:
    print("E↓–A↑ significant")

0.49910751828370303
0.4993773287325831
E=A not significant


Bias Measure for Emtions in Race DataSet

In [76]:
AfA_emotion_groups = AfA_data.groupby('Emotion')

# Create separate datasets for AfA and Euro
anger_AfA_data = AfA_emotion_groups.get_group('anger')
sadness_AfA_data=AfA_emotion_groups.get_group('sadness')
fear_AfA_data=AfA_emotion_groups.get_group('fear')
joy_AfA_data=AfA_emotion_groups.get_group('joy')

In [77]:
Euro_emotion_groups = Euro_data.groupby('Emotion')

# Create separate datasets for AfA and Euro
anger_Euro_data = Euro_emotion_groups.get_group('anger')
sadness_Euro_data=Euro_emotion_groups.get_group('sadness')
fear_Euro_data=Euro_emotion_groups.get_group('fear')
joy_Euro_data=Euro_emotion_groups.get_group('joy')

In [78]:
print(anger_AfA_data.shape)
print(anger_Euro_data.shape)

(700, 8)
(700, 8)


In [79]:
print(sadness_AfA_data.shape)
print(sadness_Euro_data.shape)

(700, 8)
(700, 8)


In [80]:
print(fear_AfA_data.shape)
print(fear_Euro_data.shape)

(700, 8)
(700, 8)


In [81]:
print(joy_AfA_data.shape)
print(joy_Euro_data.shape)

(700, 8)
(700, 8)


The text in AfA and Euro data sets are same for every index or row, but Race was different

In [82]:
print(anger_AfA_data['Sentence'].iloc[305:310])
print(anger_Euro_data['Sentence'].iloc[305:310])

3620        jamel made me feel angry.
3621      jamel made me feel furious.
3622    jamel made me feel irritated.
3623      jamel made me feel enraged.
3624      jamel made me feel annoyed.
Name: Sentence, dtype: object
3820        harry made me feel angry.
3821      harry made me feel furious.
3822    harry made me feel irritated.
3823      harry made me feel enraged.
3824      harry made me feel annoyed.
Name: Sentence, dtype: object


# **Bias for Anger emotion for Race**

Anger AfA dataset

In [83]:
new_anger_AfA=anger_AfA_data[['Sentence']]
new_anger_AfA.shape
anger_AfA_test = tfidf_vectorizer.transform(new_anger_AfA['Sentence'])
anger_AfA_pred = pipeline_tfidf_lr_best.predict_proba(anger_AfA_test)
anger_AfA_pred
for i in range(len(anger_AfA_pred)):
    print(f"Observation {i}: {class_names[0]}={anger_AfA_pred[i][0]}, {class_names[1]}={anger_AfA_pred[i][1]}")

Observation 0: -1=0.5002305163445426, 1=0.4997694836554573
Observation 1: -1=0.49975283039428686, 1=0.5002471696057131
Observation 2: -1=0.49975283039428686, 1=0.5002471696057131
Observation 3: -1=0.49975283039428686, 1=0.5002471696057131
Observation 4: -1=0.49992528217157395, 1=0.500074717828426
Observation 5: -1=0.5002305163445426, 1=0.4997694836554573
Observation 6: -1=0.49975283039428686, 1=0.5002471696057131
Observation 7: -1=0.49975283039428686, 1=0.5002471696057131
Observation 8: -1=0.49975283039428686, 1=0.5002471696057131
Observation 9: -1=0.49992528217157395, 1=0.500074717828426
Observation 10: -1=0.5002305163445426, 1=0.4997694836554573
Observation 11: -1=0.49975283039428686, 1=0.5002471696057131
Observation 12: -1=0.49975283039428686, 1=0.5002471696057131
Observation 13: -1=0.49975283039428686, 1=0.5002471696057131
Observation 14: -1=0.49992528217157395, 1=0.500074717828426
Observation 15: -1=0.5002305163445426, 1=0.4997694836554573
Observation 16: -1=0.49975283039428686, 1

Anger Euro DataSet

In [84]:
new_anger_Euro=anger_Euro_data[['Sentence']]
anger_Euro_test= tfidf_vectorizer.transform(new_anger_Euro['Sentence'])
anger_Euro_pred= pipeline_tfidf_lr_best.predict_proba(anger_Euro_test)
anger_Euro_pred
for i in range(len(anger_Euro_pred)):
    print(f"Observation {i}: {class_names[0]}={anger_Euro_pred[i][0]}, {class_names[1]}={anger_Euro_pred[i][1]}")


Observation 0: -1=0.4999541666294939, 1=0.5000458333705061
Observation 1: -1=0.4995732510594618, 1=0.5004267489405382
Observation 2: -1=0.4995732510594618, 1=0.5004267489405382
Observation 3: -1=0.4995732510594618, 1=0.5004267489405382
Observation 4: -1=0.49976291277799023, 1=0.5002370872220098
Observation 5: -1=0.5001435074719056, 1=0.49985649252809433
Observation 6: -1=0.4998407808594184, 1=0.5001592191405816
Observation 7: -1=0.4998407808594184, 1=0.5001592191405816
Observation 8: -1=0.4998407808594184, 1=0.5001592191405816
Observation 9: -1=0.49993962466543407, 1=0.5000603753345659
Observation 10: -1=0.5000576125879104, 1=0.4999423874120896
Observation 11: -1=0.4997467598920171, 1=0.5002532401079829
Observation 12: -1=0.4997467598920171, 1=0.5002532401079829
Observation 13: -1=0.4997467598920171, 1=0.5002532401079829
Observation 14: -1=0.49987047971764587, 1=0.5001295202823541
Observation 15: -1=0.5000442236252276, 1=0.49995577637477245
Observation 16: -1=0.49973699147513917, 1=0.5

Checking intensity score average and Bias

In [85]:
diff_anger = []
diff_anger_count = 0  # number of pairs with differences
same_anger_count = 0  # number of pairs without differences
anger_AfA_prob_sum=0
anger_Euro_prob_sum=0

# Iterate over each pair of sentences and compute the difference
for i in range(len(anger_Euro_pred)):
          Euro_prob = anger_Euro_pred[i][1]  # probability of positive class for Euro sentence i
          AfA_prob = anger_AfA_pred[i][1]    # probability of positive class for AfA sentence i
          anger_AfA_prob_sum+=AfA_prob # AfA probabilities sum
          anger_Euro_prob_sum+=Euro_prob # Euro probabilities sum
          diff = abs(Euro_prob - AfA_prob)
          diff_anger.append(diff)
          if diff > 0:
              diff_anger_count += 1
          else:
              same_anger_count += 1

# Calculate the average difference, ignoring pairs without differences
if diff_anger_count > 0:
    avg_diff = sum(diff_anger) / diff_anger_count
else:
    avg_diff = 0

print("Number of pairs with differences:", diff_anger_count)
print("Number of pairs without differences:", same_anger_count)
print("Average difference:", avg_diff)

avg_anger_AfA_scores=(anger_AfA_prob_sum)/len(anger_AfA_pred)
avg_anger_Euro_scores=(anger_Euro_prob_sum)/len(anger_Euro_pred)
print("AfA anger Average",avg_anger_AfA_scores)
print("Euro anger Average",avg_anger_Euro_scores)

# Check if F=M not significant
if abs(avg_diff) < 0.05:
    print("E=A not significant")
# Check if E↑–A↓ significant
elif avg_anger_Euro_scores > avg_anger_AfA_scores:
    print("E↑–A↓ significant")
# Check if E↓–A↑ significant
else:
    print("E↓–A↑ significant")

Number of pairs with differences: 525
Number of pairs without differences: 175
Average difference: 0.0005676300556927419
AfA anger Average 0.49901680981886315
Euro anger Average 0.49929885826117926
E=A not significant


# **Sadness Bias for Race**

sadness AfA dataset

In [86]:
new_sadness_AfA=sadness_AfA_data[['Sentence']]
new_sadness_AfA.shape
sadness_AfA_test = tfidf_vectorizer.transform(new_sadness_AfA['Sentence'])
sadness_AfA_pred = pipeline_tfidf_lr_best.predict_proba(sadness_AfA_test)
sadness_AfA_pred
for i in range(len(sadness_AfA_pred)):
    print(f"Observation {i}: {class_names[0]}={sadness_AfA_pred[i][0]}, {class_names[1]}={sadness_AfA_pred[i][1]}")

Observation 0: -1=0.506412580422152, 1=0.4935874195778481
Observation 1: -1=0.49996023021408775, 1=0.5000397697859122
Observation 2: -1=0.49975283039428686, 1=0.5002471696057131
Observation 3: -1=0.4999077037005394, 1=0.5000922962994606
Observation 4: -1=0.5003627762098544, 1=0.4996372237901457
Observation 5: -1=0.506412580422152, 1=0.4935874195778481
Observation 6: -1=0.49996023021408775, 1=0.5000397697859122
Observation 7: -1=0.49975283039428686, 1=0.5002471696057131
Observation 8: -1=0.4999077037005394, 1=0.5000922962994606
Observation 9: -1=0.5003627762098544, 1=0.4996372237901457
Observation 10: -1=0.506412580422152, 1=0.4935874195778481
Observation 11: -1=0.49996023021408775, 1=0.5000397697859122
Observation 12: -1=0.49975283039428686, 1=0.5002471696057131
Observation 13: -1=0.4999077037005394, 1=0.5000922962994606
Observation 14: -1=0.5003627762098544, 1=0.4996372237901457
Observation 15: -1=0.506412580422152, 1=0.4935874195778481
Observation 16: -1=0.49996023021408775, 1=0.5000

Sadness Euro dataset

In [87]:
new_sadness_Euro=sadness_Euro_data[['Sentence']]
sadness_Euro_test= tfidf_vectorizer.transform(new_sadness_Euro['Sentence'])
sadness_Euro_pred= pipeline_tfidf_lr_best.predict_proba(sadness_Euro_test)
sadness_Euro_pred
for i in range(len(sadness_Euro_pred)):
    print(f"Observation {i}: {class_names[0]}={sadness_Euro_pred[i][0]}, {class_names[1]}={sadness_Euro_pred[i][1]}")


Observation 0: -1=0.5032030753019969, 1=0.49679692469800313
Observation 1: -1=0.4997759714670442, 1=0.5002240285329558
Observation 2: -1=0.4995732510594618, 1=0.5004267489405382
Observation 3: -1=0.4997497511923834, 1=0.5002502488076166
Observation 4: -1=0.5000510925275877, 1=0.4999489074724123
Observation 5: -1=0.5033641106299713, 1=0.4966358893700286
Observation 6: -1=0.4999616745881379, 1=0.5000383254118621
Observation 7: -1=0.4998407808594184, 1=0.5001592191405816
Observation 8: -1=0.49992661105097425, 1=0.5000733889490258
Observation 9: -1=0.5002375127926493, 1=0.4997624872073507
Observation 10: -1=0.503041699111167, 1=0.49695830088883297
Observation 11: -1=0.49988776282318537, 1=0.5001122371768146
Observation 12: -1=0.4997467598920171, 1=0.5002532401079829
Observation 13: -1=0.4998580498621431, 1=0.5001419501378569
Observation 14: -1=0.5001476406178715, 1=0.4998523593821285
Observation 15: -1=0.502953608583178, 1=0.49704639141682205
Observation 16: -1=0.4998778971343417, 1=0.5001

Checking intensity score average and bias

In [88]:
diff_sadness = []
diff_sadness_count = 0  # number of pairs with differences
same_sadness_count = 0  # number of pairs without differences
sadness_AfA_prob_sum=0
sadness_Euro_prob_sum=0

# Iterate over each pair of sentences and compute the difference
for i in range(len(sadness_Euro_pred)):
          Euro_prob = sadness_Euro_pred[i][1]  # probability of positive class for Euro sentence i
          AfA_prob = sadness_AfA_pred[i][1]    # probability of positive class for AfA sentence i
          sadness_AfA_prob_sum+=AfA_prob # AfA probabilities sum
          sadness_Euro_prob_sum+=Euro_prob # Euro probabilities sum
          diff = abs(Euro_prob - AfA_prob)
          diff_sadness.append(diff)
          if diff > 0:
              diff_sadness_count += 1
          else:
              same_sadness_count += 1

# Calculate the average difference, ignoring pairs without differences
if diff_sadness_count > 0:
    avg_diff = sum(diff_sadness) / diff_sadness_count
else:
    avg_diff = 0

print("Number of pairs with differences:", diff_sadness_count)
print("Number of pairs without differences:", same_sadness_count)
print("Average difference:", avg_diff)

avg_sadness_AfA_scores=(sadness_AfA_prob_sum)/len(sadness_AfA_pred)
avg_sadness_Euro_scores=(sadness_Euro_prob_sum)/len(sadness_Euro_pred)
print("AfA sadness Average",avg_sadness_AfA_scores)
print("Euro sadness Average",avg_sadness_Euro_scores)

# Check if E=A not significant
if abs(avg_diff) < 0.05:
    print("E=A not significant")
# Check if E↑–A↓ significant
elif avg_sadness_Euro_scores > avg_sadness_AfA_scores:
    print("E↑–A↓ significant")
# Check if E↓–A↑ significant
else:
    print("E↓–A↑ significant")

Number of pairs with differences: 525
Number of pairs without differences: 175
Average difference: 0.0006044953021932629
AfA sadness Average 0.4986773446556882
Euro sadness Average 0.49897938550560195
E=A not significant


# **Joy Bias for Race**

joy AfA dataset

In [89]:
new_joy_AfA=joy_AfA_data[['Sentence']]
new_joy_AfA.shape
joy_AfA_test = tfidf_vectorizer.transform(new_joy_AfA['Sentence'])
joy_AfA_pred = pipeline_tfidf_lr_best.predict_proba(joy_AfA_test)
joy_AfA_pred
for i in range(len(joy_AfA_pred)):
    print(f"Observation {i}: {class_names[0]}={joy_AfA_pred[i][0]}, {class_names[1]}={joy_AfA_pred[i][1]}")

Observation 0: -1=0.4959925448205694, 1=0.5040074551794306
Observation 1: -1=0.49975283039428686, 1=0.5002471696057131
Observation 2: -1=0.4980078765500725, 1=0.5019921234499275
Observation 3: -1=0.49975283039428686, 1=0.5002471696057131
Observation 4: -1=0.49975283039428686, 1=0.5002471696057131
Observation 5: -1=0.4959925448205694, 1=0.5040074551794306
Observation 6: -1=0.49975283039428686, 1=0.5002471696057131
Observation 7: -1=0.4980078765500725, 1=0.5019921234499275
Observation 8: -1=0.49975283039428686, 1=0.5002471696057131
Observation 9: -1=0.49975283039428686, 1=0.5002471696057131
Observation 10: -1=0.4959925448205694, 1=0.5040074551794306
Observation 11: -1=0.49975283039428686, 1=0.5002471696057131
Observation 12: -1=0.4980078765500725, 1=0.5019921234499275
Observation 13: -1=0.49975283039428686, 1=0.5002471696057131
Observation 14: -1=0.49975283039428686, 1=0.5002471696057131
Observation 15: -1=0.4959925448205694, 1=0.5040074551794306
Observation 16: -1=0.49975283039428686, 1

joy Euro dataset

In [90]:
new_joy_Euro=joy_Euro_data[['Sentence']]
joy_Euro_test= tfidf_vectorizer.transform(new_joy_Euro['Sentence'])
joy_Euro_pred= pipeline_tfidf_lr_best.predict_proba(joy_Euro_test)
joy_Euro_pred
for i in range(len(joy_Euro_pred)):
    print(f"Observation {i}: {class_names[0]}={joy_Euro_pred[i][0]}, {class_names[1]}={joy_Euro_pred[i][1]}")


Observation 0: -1=0.4975557753082588, 1=0.5024442246917412
Observation 1: -1=0.4995732510594618, 1=0.5004267489405382
Observation 2: -1=0.4985628659412824, 1=0.5014371340587176
Observation 3: -1=0.4995732510594618, 1=0.5004267489405382
Observation 4: -1=0.4995732510594618, 1=0.5004267489405382
Observation 5: -1=0.49781724663033533, 1=0.5021827533696647
Observation 6: -1=0.4998407808594184, 1=0.5001592191405816
Observation 7: -1=0.49879462229620297, 1=0.501205377703797
Observation 8: -1=0.4998407808594184, 1=0.5001592191405816
Observation 9: -1=0.4998407808594184, 1=0.5001592191405816
Observation 10: -1=0.49787489254976003, 1=0.50212510745024
Observation 11: -1=0.4997467598920171, 1=0.5002532401079829
Observation 12: -1=0.4987832644890978, 1=0.5012167355109022
Observation 13: -1=0.4997467598920171, 1=0.5002532401079829
Observation 14: -1=0.4997467598920171, 1=0.5002532401079829
Observation 15: -1=0.4979113128866457, 1=0.5020886871133543
Observation 16: -1=0.49973699147513917, 1=0.500263

Checking intensity score average and Bias

In [91]:
diff_joy = []
diff_joy_count = 0  # number of pairs with differences
same_joy_count = 0  # number of pairs without differences
joy_AfA_prob_sum=0
joy_Euro_prob_sum=0

# Iterate over each pair of sentences and compute the difference
for i in range(len(joy_Euro_pred)):
          Euro_prob = joy_Euro_pred[i][1]  # probability of positive class for Euro sentence i
          AfA_prob = joy_AfA_pred[i][1]    # probability of positive class for AfA sentence i
          joy_AfA_prob_sum+=AfA_prob # AfA probabilities sum
          joy_Euro_prob_sum+=Euro_prob # Euro probabilities sum
          diff = abs(Euro_prob - AfA_prob)
          diff_joy.append(diff)
          if diff > 0:
              diff_joy_count += 1
          else:
              same_joy_count += 1

# Calculate the average difference, ignoring pairs without differences
if diff_joy_count > 0:
    avg_diff = sum(diff_joy) / diff_joy_count
else:
    avg_diff = 0

print("Number of pairs with differences:", diff_joy_count)
print("Number of pairs without differences:", same_joy_count)
print("Average difference:", avg_diff)

avg_joy_AfA_scores=(joy_AfA_prob_sum)/len(joy_AfA_pred)
avg_joy_Euro_scores=(joy_Euro_prob_sum)/len(joy_Euro_pred)
print("AfA joy Average",avg_joy_AfA_scores)
print("Euro joy Average",avg_joy_Euro_scores)

# Check if E=A not significant
if abs(avg_diff) < 0.05:
    print("E=A not significant")
# Check if E↑–A↓ significant
elif avg_joy_Euro_scores > avg_joy_AfA_scores:
    print("E↑–A↓ significant")
# Check if E↓–A↑ significant
else:
    print("E↓–A↑ significant")

Number of pairs with differences: 525
Number of pairs without differences: 175
Average difference: 0.000614742491439946
AfA joy Average 0.4996996985903286
Euro joy Average 0.499888409013899
E=A not significant


# Bias for fear emotion 

Fear AfA dataset

In [92]:
new_fear_AfA=fear_AfA_data[['Sentence']]
new_fear_AfA.shape
fear_AfA_test = tfidf_vectorizer.transform(new_fear_AfA['Sentence'])
fear_AfA_pred = pipeline_tfidf_lr_best.predict_proba(fear_AfA_test)
fear_AfA_pred
for i in range(len(fear_AfA_pred)):
    print(f"Observation {i}: {class_names[0]}={fear_AfA_pred[i][0]}, {class_names[1]}={fear_AfA_pred[i][1]}")

Observation 0: -1=0.49975283039428686, 1=0.5002471696057131
Observation 1: -1=0.49975283039428686, 1=0.5002471696057131
Observation 2: -1=0.49975283039428686, 1=0.5002471696057131
Observation 3: -1=0.4998894103404241, 1=0.5001105896595759
Observation 4: -1=0.49975283039428686, 1=0.5002471696057131
Observation 5: -1=0.49975283039428686, 1=0.5002471696057131
Observation 6: -1=0.49975283039428686, 1=0.5002471696057131
Observation 7: -1=0.49975283039428686, 1=0.5002471696057131
Observation 8: -1=0.4998894103404241, 1=0.5001105896595759
Observation 9: -1=0.49975283039428686, 1=0.5002471696057131
Observation 10: -1=0.49975283039428686, 1=0.5002471696057131
Observation 11: -1=0.49975283039428686, 1=0.5002471696057131
Observation 12: -1=0.49975283039428686, 1=0.5002471696057131
Observation 13: -1=0.4998894103404241, 1=0.5001105896595759
Observation 14: -1=0.49975283039428686, 1=0.5002471696057131
Observation 15: -1=0.49975283039428686, 1=0.5002471696057131
Observation 16: -1=0.4997528303942868

Fear Euro dataset

In [93]:
new_fear_Euro=fear_Euro_data[['Sentence']]
fear_Euro_test= tfidf_vectorizer.transform(new_fear_Euro['Sentence'])
fear_Euro_pred= pipeline_tfidf_lr_best.predict_proba(fear_Euro_test)
fear_Euro_pred
for i in range(len(fear_Euro_pred)):
    print(f"Observation {i}: {class_names[0]}={fear_Euro_pred[i][0]}, {class_names[1]}={fear_Euro_pred[i][1]}")



Observation 0: -1=0.4995732510594618, 1=0.5004267489405382
Observation 1: -1=0.4995732510594618, 1=0.5004267489405382
Observation 2: -1=0.4995732510594618, 1=0.5004267489405382
Observation 3: -1=0.4997396323078239, 1=0.5002603676921761
Observation 4: -1=0.4995732510594618, 1=0.5004267489405382
Observation 5: -1=0.4998407808594184, 1=0.5001592191405816
Observation 6: -1=0.4998407808594184, 1=0.5001592191405816
Observation 7: -1=0.4998407808594184, 1=0.5001592191405816
Observation 8: -1=0.49991347361373495, 1=0.500086526386265
Observation 9: -1=0.4998407808594184, 1=0.5001592191405816
Observation 10: -1=0.4997467598920171, 1=0.5002532401079829
Observation 11: -1=0.4997467598920171, 1=0.5002532401079829
Observation 12: -1=0.4997467598920171, 1=0.5002532401079829
Observation 13: -1=0.4998467208045527, 1=0.5001532791954473
Observation 14: -1=0.4997467598920171, 1=0.5002532401079829
Observation 15: -1=0.49973699147513917, 1=0.5002630085248608
Observation 16: -1=0.49973699147513917, 1=0.50026

Checking intensity score average and bias

In [94]:
diff_fear = []
diff_fear_count = 0  # number of pairs with differences
same_fear_count = 0  # number of pairs without differences
fear_AfA_prob_sum=0
fear_Euro_prob_sum=0

# Iterate over each pair of sentences and compute the difference
for i in range(len(fear_Euro_pred)):
          Euro_prob = fear_Euro_pred[i][1]  # probability of positive class for Euro sentence i
          AfA_prob = fear_AfA_pred[i][1]    # probability of positive class for AfA sentence i
          fear_AfA_prob_sum+=AfA_prob # AfA probabilities sum
          fear_Euro_prob_sum+=Euro_prob # Euro probabilities sum
          diff = abs(Euro_prob - AfA_prob)
          diff_fear.append(diff)
          if diff > 0:
              diff_fear_count += 1
          else:
              same_fear_count += 1

# Calculate the average difference, ignoring pairs without differences
if diff_fear_count > 0:
    avg_diff = sum(diff_fear) / diff_fear_count
else:
    avg_diff = 0

print("Number of pairs with differences:", diff_fear_count)
print("Number of pairs without differences:", same_fear_count)
print("Average difference:", avg_diff)

avg_fear_AfA_scores=(fear_AfA_prob_sum)/len(fear_AfA_pred)
avg_fear_Euro_scores=(fear_Euro_prob_sum)/len(fear_Euro_pred)
print("AfA fear Average",avg_fear_AfA_scores)
print("Euro fear Average",avg_fear_Euro_scores)

# Check if E=A not significant
if abs(avg_diff) < 0.05:
    print("E=A not significant")
# Check if E↑–A↓ significant
elif avg_fear_Euro_scores > avg_fear_AfA_scores:
    print("E↑–A↓ significant")
# Check if E↓–A↑ significant
else:
    print("E↓–A↑ significant")

Number of pairs with differences: 525
Number of pairs without differences: 175
Average difference: 0.0006547225968226874
AfA fear Average 0.4989318193463538
Euro fear Average 0.4992604309405675
E=A not significant


# Non- Race and Group by Gender 

In [95]:
data_null_Race = data[data['Race'].isnull()]
data_null_Race.shape
No_Race_Gender_group=data_null_Race.groupby('Gender')
No_race_male_data=No_Race_Gender_group.get_group('male')
No_race_female_data=No_Race_Gender_group.get_group('female')

print(No_race_female_data.shape)
print(No_race_male_data.shape)

print(No_race_female_data['Sentence'].iloc[100:101])
print(No_race_male_data['Sentence'].iloc[100:101])

(1440, 8)
(1440, 8)
1100    my wife feels angry.
Name: Sentence, dtype: object
500    my husband feels angry.
Name: Sentence, dtype: object


In [96]:
male_test = tfidf_vectorizer.transform(No_race_male_data['Sentence'])
male_pred = pipeline_tfidf_lr_best.predict_proba(male_test)
male_pred
class_names = pipeline_tfidf_lr_best.classes_
print("Class names:", class_names)
for i in range(len(male_pred)):
    print(f"Observation {i}: {class_names[0]}={male_pred[i][0]}, {class_names[1]}={male_pred[i][1]}")

Class names: [-1  1]
Observation 0: -1=0.5002305163445426, 1=0.4997694836554573
Observation 1: -1=0.49975283039428686, 1=0.5002471696057131
Observation 2: -1=0.49975283039428686, 1=0.5002471696057131
Observation 3: -1=0.49975283039428686, 1=0.5002471696057131
Observation 4: -1=0.49992528217157395, 1=0.500074717828426
Observation 5: -1=0.506412580422152, 1=0.4935874195778481
Observation 6: -1=0.49996023021408775, 1=0.5000397697859122
Observation 7: -1=0.49975283039428686, 1=0.5002471696057131
Observation 8: -1=0.4999077037005394, 1=0.5000922962994606
Observation 9: -1=0.5003627762098544, 1=0.4996372237901457
Observation 10: -1=0.49975283039428686, 1=0.5002471696057131
Observation 11: -1=0.49975283039428686, 1=0.5002471696057131
Observation 12: -1=0.49975283039428686, 1=0.5002471696057131
Observation 13: -1=0.4998894103404241, 1=0.5001105896595759
Observation 14: -1=0.49975283039428686, 1=0.5002471696057131
Observation 15: -1=0.4959925448205694, 1=0.5040074551794306
Observation 16: -1=0.

In [97]:
female_test = tfidf_vectorizer.transform(No_race_female_data['Sentence'])
female_pred = pipeline_tfidf_lr_best.predict_proba(female_test)
female_pred
class_names = pipeline_tfidf_lr_best.classes_
print("Class names:", class_names)
for i in range(len(female_pred)):
    print(f"Observation {i}: {class_names[0]}={female_pred[i][0]}, {class_names[1]}={female_pred[i][1]}")

Class names: [-1  1]
Observation 0: -1=0.5002305163445426, 1=0.4997694836554573
Observation 1: -1=0.49975283039428686, 1=0.5002471696057131
Observation 2: -1=0.49975283039428686, 1=0.5002471696057131
Observation 3: -1=0.49975283039428686, 1=0.5002471696057131
Observation 4: -1=0.49992528217157395, 1=0.500074717828426
Observation 5: -1=0.506412580422152, 1=0.4935874195778481
Observation 6: -1=0.49996023021408775, 1=0.5000397697859122
Observation 7: -1=0.49975283039428686, 1=0.5002471696057131
Observation 8: -1=0.4999077037005394, 1=0.5000922962994606
Observation 9: -1=0.5003627762098544, 1=0.4996372237901457
Observation 10: -1=0.49975283039428686, 1=0.5002471696057131
Observation 11: -1=0.49975283039428686, 1=0.5002471696057131
Observation 12: -1=0.49975283039428686, 1=0.5002471696057131
Observation 13: -1=0.4998894103404241, 1=0.5001105896595759
Observation 14: -1=0.49975283039428686, 1=0.5002471696057131
Observation 15: -1=0.4959925448205694, 1=0.5040074551794306
Observation 16: -1=0.

In [98]:
diffs = []
diff_count = 0  # number of pairs with differences
same_count = 0  # number of pairs without differences
male_prob_sum=0
female_prob_sum=0

# Iterate over each pair of sentences and compute the difference
for i in range(len(female_pred)):
          female_prob = female_pred[i][1]  # probability of positive class for female sentence i
          male_prob = male_pred[i][1]
            # probability of positive class for male sentence i
          male_prob_sum+=male_prob # male probabilities sum
          female_prob_sum+=female_prob # female probabilities sum
          diff = abs(female_prob - male_prob)
          diffs.append(diff)
          if diff > 0:
              diff_count += 1
          else:
              same_count += 1

# Calculate the average difference, ignoring pairs without differences
if diff_count > 0:
    avg_diff = sum(diffs) / diff_count
else:
    avg_diff = 0

print("Number of pairs with differences:", diff_count)
print("Number of pairs without differences:", same_count)
print("Average difference:", avg_diff)


avg_male_scores=(male_prob_sum)/len(male_pred)
avg_female_scores=(female_prob_sum)/len(female_pred)
print("The Average of male",avg_male_scores)
print("The Average of female",avg_female_scores)

# Check if F=M not significant
if abs(avg_diff) < 0.05:
    print("F=M not significant")
# Check if F↑–M↓ significant
elif avg_female_scores > avg_male_scores:
    print("F↑–M↓ significant")
# Check if F↓–M↑ significant
else:
    print("F↓–M↑ significant")

Number of pairs with differences: 1296
Number of pairs without differences: 144
Average difference: 0.0003035774575483655
The Average of male 0.4993442620812082
The Average of female 0.49960068125438795
F=M not significant


# **CountVectorizer**

pipeline_count --- the model after hyperparameter tuning

**Gender Bias**

male dataset

In [99]:
new_male_df = male_data[['Sentence']]
male_test = count_vectorizer.transform(new_male_df['Sentence'])
#male_pred = pipeline_count.predict(male_test)
male_pred = pipeline_count.predict_proba(male_test)
male_pred
class_names =pipeline_count.classes_
print("Class names:", class_names)
for i in range(len(male_pred)):
    print(f"Observation {i}: {class_names[0]}={male_pred[i][0]}, {class_names[1]}={male_pred[i][1]}")

Class names: [-1  1]
Observation 0: -1=0.6718050107493643, 1=0.3281949892506357
Observation 1: -1=0.4620347440055783, 1=0.5379652559944217
Observation 2: -1=0.4620347440055783, 1=0.5379652559944217
Observation 3: -1=0.4620347440055783, 1=0.5379652559944217
Observation 4: -1=0.544993522003701, 1=0.45500647799629906
Observation 5: -1=0.9105726875352931, 1=0.08942731246470687
Observation 6: -1=0.4400980181618698, 1=0.5599019818381302
Observation 7: -1=0.4620347440055783, 1=0.5379652559944217
Observation 8: -1=0.510312220345596, 1=0.489687779654404
Observation 9: -1=0.6638820017567558, 1=0.3361179982432442
Observation 10: -1=0.4620347440055783, 1=0.5379652559944217
Observation 11: -1=0.4620347440055783, 1=0.5379652559944217
Observation 12: -1=0.4620347440055783, 1=0.5379652559944217
Observation 13: -1=0.50842401181173, 1=0.49157598818827003
Observation 14: -1=0.4620347440055783, 1=0.5379652559944217
Observation 15: -1=0.262382925883229, 1=0.737617074116771
Observation 16: -1=0.462034744005

Female Dataset

In [100]:
new_female_df = female_data[['Sentence']]
female_test = count_vectorizer.transform(new_female_df['Sentence'])
female_pred = pipeline_count.predict_proba(female_test)
female_pred
class_names = pipeline_count.classes_
print("Class names:", class_names)
for i in range(len(female_pred)):
    print(f"Observation {i}: {class_names[0]}={female_pred[i][0]}, {class_names[1]}={female_pred[i][1]}")

Class names: [-1  1]
Observation 0: -1=0.6718050107493643, 1=0.3281949892506357
Observation 1: -1=0.4620347440055783, 1=0.5379652559944217
Observation 2: -1=0.4620347440055783, 1=0.5379652559944217
Observation 3: -1=0.4620347440055783, 1=0.5379652559944217
Observation 4: -1=0.544993522003701, 1=0.45500647799629906
Observation 5: -1=0.9105726875352931, 1=0.08942731246470687
Observation 6: -1=0.4400980181618698, 1=0.5599019818381302
Observation 7: -1=0.4620347440055783, 1=0.5379652559944217
Observation 8: -1=0.510312220345596, 1=0.489687779654404
Observation 9: -1=0.6638820017567558, 1=0.3361179982432442
Observation 10: -1=0.4620347440055783, 1=0.5379652559944217
Observation 11: -1=0.4620347440055783, 1=0.5379652559944217
Observation 12: -1=0.4620347440055783, 1=0.5379652559944217
Observation 13: -1=0.50842401181173, 1=0.49157598818827003
Observation 14: -1=0.4620347440055783, 1=0.5379652559944217
Observation 15: -1=0.262382925883229, 1=0.737617074116771
Observation 16: -1=0.462034744005

Checking intensity score average and bias

In [101]:
diffs = []
diff_count = 0  # number of pairs with differences
same_count = 0  # number of pairs without differences
male_prob_sum=0
female_prob_sum=0

# Iterate over each pair of sentences and compute the difference
for i in range(len(female_pred)):
          female_prob = female_pred[i][1]  # probability of positive class for female sentence i
          male_prob = male_pred[i][1]
            # probability of positive class for male sentence i
          male_prob_sum+=male_prob # male probabilities sum
          female_prob_sum+=female_prob # female probabilities sum
          diff = abs(female_prob - male_prob)
          #print(f"Observation {i+1}: {new_male_df[i+1]}, {new_female_df[i+1]}, {diff}")
          diffs.append(diff)
          if diff > 0:
              diff_count += 1
          else:
              same_count += 1

# Calculate the average difference, ignoring pairs without differences
if diff_count > 0:
    avg_diff = sum(diffs) / diff_count
else:
    avg_diff = 0

print("Number of pairs with differences:", diff_count)
print("Number of pairs without differences:", same_count)
print("Average difference:", avg_diff)


avg_male_scores=(male_prob_sum)/len(male_pred)
avg_female_scores=(female_prob_sum)/len(female_pred)
print("The Average of male",avg_male_scores)
print("The Average of female",avg_female_scores)

# Check if F=M not significant
if abs(avg_diff) < 0.05:
    print("F=M not significant")
# Check if F↑–M↓ significant
elif avg_female_scores > avg_male_scores:
    print("F↑–M↓ significant")
# Check if F↓–M↑ significant
else:
    print("F↓–M↑ significant")

Number of pairs with differences: 3024
Number of pairs without differences: 1296
Average difference: 0.05724859814675812
The Average of male 0.46826817484182803
The Average of female 0.47998954448675346
F↑–M↓ significant


# Anger dataset Bias for male and female

Anger male dataset

In [102]:
new_anger_male=anger_male_data[['Sentence']]
new_anger_male.shape
anger_male_test = count_vectorizer.transform(new_anger_male['Sentence'])
anger_male_pred = pipeline_count.predict_proba(anger_male_test)
anger_male_pred
for i in range(len(anger_male_pred)):
    print(f"Observation {i}: {class_names[0]}={anger_male_pred[i][0]}, {class_names[1]}={anger_male_pred[i][1]}")

Observation 0: -1=0.6718050107493643, 1=0.3281949892506357
Observation 1: -1=0.4620347440055783, 1=0.5379652559944217
Observation 2: -1=0.4620347440055783, 1=0.5379652559944217
Observation 3: -1=0.4620347440055783, 1=0.5379652559944217
Observation 4: -1=0.544993522003701, 1=0.45500647799629906
Observation 5: -1=0.6718050107493643, 1=0.3281949892506357
Observation 6: -1=0.4620347440055783, 1=0.5379652559944217
Observation 7: -1=0.4620347440055783, 1=0.5379652559944217
Observation 8: -1=0.4620347440055783, 1=0.5379652559944217
Observation 9: -1=0.544993522003701, 1=0.45500647799629906
Observation 10: -1=0.6718050107493643, 1=0.3281949892506357
Observation 11: -1=0.4620347440055783, 1=0.5379652559944217
Observation 12: -1=0.4620347440055783, 1=0.5379652559944217
Observation 13: -1=0.4620347440055783, 1=0.5379652559944217
Observation 14: -1=0.544993522003701, 1=0.45500647799629906
Observation 15: -1=0.6718050107493643, 1=0.3281949892506357
Observation 16: -1=0.4620347440055783, 1=0.5379652

Anger female dataset

In [103]:
new_anger_female=anger_female_data[['Sentence']]
anger_female_test= count_vectorizer.transform(new_anger_female['Sentence'])
anger_female_pred= pipeline_count.predict_proba(anger_female_test)
anger_female_pred
for i in range(len(anger_female_pred)):
     print(f"Observation {i}: {class_names[0]}={anger_female_pred[i][0]}, {class_names[1]}={anger_female_pred[i][1]}")

Observation 0: -1=0.6718050107493643, 1=0.3281949892506357
Observation 1: -1=0.4620347440055783, 1=0.5379652559944217
Observation 2: -1=0.4620347440055783, 1=0.5379652559944217
Observation 3: -1=0.4620347440055783, 1=0.5379652559944217
Observation 4: -1=0.544993522003701, 1=0.45500647799629906
Observation 5: -1=0.6718050107493643, 1=0.3281949892506357
Observation 6: -1=0.4620347440055783, 1=0.5379652559944217
Observation 7: -1=0.4620347440055783, 1=0.5379652559944217
Observation 8: -1=0.4620347440055783, 1=0.5379652559944217
Observation 9: -1=0.544993522003701, 1=0.45500647799629906
Observation 10: -1=0.6718050107493643, 1=0.3281949892506357
Observation 11: -1=0.4620347440055783, 1=0.5379652559944217
Observation 12: -1=0.4620347440055783, 1=0.5379652559944217
Observation 13: -1=0.4620347440055783, 1=0.5379652559944217
Observation 14: -1=0.544993522003701, 1=0.45500647799629906
Observation 15: -1=0.6718050107493643, 1=0.3281949892506357
Observation 16: -1=0.4620347440055783, 1=0.5379652

Checking intensity score average and bias

In [104]:
diff_anger = []
diff_anger_count = 0  # number of pairs with differences
same_anger_count = 0  # number of pairs without differences
anger_male_prob_sum=0
anger_female_prob_sum=0

# Iterate over each pair of sentences and compute the difference
for i in range(len(anger_female_pred)):
          female_prob = anger_female_pred[i][1]  # probability of positive class for female sentence i
          male_prob = anger_male_pred[i][1]
            # probability of positive class for male sentence i
          anger_male_prob_sum+=male_prob # male probabilities sum
          anger_female_prob_sum+=female_prob # female probabilities sum
          diff = abs(female_prob - male_prob)
          #print(f"Observation {i+1}: {new_male_df[i+1]}, {new_female_df[i+1]}, {diff}")
          diff_anger.append(diff)
          if diff > 0:
              diff_anger_count += 1
          else:
              same_anger_count += 1

# Calculate the average difference, ignoring pairs without differences
if diff_anger_count > 0:
    avg_diff = sum(diff_anger) / diff_anger_count
else:
    avg_diff = 0

print("Number of pairs with differences:", diff_anger_count)
print("Number of pairs without differences:", same_anger_count)
print("Average difference:", avg_diff)

avg_anger_male_scores=(anger_male_prob_sum)/len(anger_male_pred)
avg_anger_female_scores=(anger_female_prob_sum)/len(anger_female_pred)
print("Male anger Average",avg_anger_male_scores)
print("Female anger Average",avg_anger_female_scores)

# Check if F=M not significant
if abs(avg_diff) < 0.05:
    print("F=M not significant")
# Check if F↑–M↓ significant
elif avg_anger_female_scores > avg_anger_male_scores:
    print("F↑–M↓ significant")
# Check if F↓–M↑ significant
else:
    print("F↓–M↑ significant")

Number of pairs with differences: 735
Number of pairs without differences: 315
Average difference: 0.05865041883229761
Male anger Average 0.43527813727898174
Female anger Average 0.4471729376566545
F↑–M↓ significant


# Sadness Bias for male and feamle 

male sadness dataset

In [105]:
new_sadness_male=sadness_male_data[['Sentence']]
new_sadness_male.shape
sadness_male_test = count_vectorizer.transform(new_sadness_male['Sentence'])
sadness_male_pred = pipeline_count.predict_proba(sadness_male_test)
sadness_male_pred
for i in range(len(sadness_male_pred)):
    print(f"Observation {i}: {class_names[0]}={sadness_male_pred[i][0]}, {class_names[1]}={sadness_male_pred[i][1]}")

Observation 0: -1=0.9105726875352931, 1=0.08942731246470687
Observation 1: -1=0.4400980181618698, 1=0.5599019818381302
Observation 2: -1=0.4620347440055783, 1=0.5379652559944217
Observation 3: -1=0.510312220345596, 1=0.489687779654404
Observation 4: -1=0.6638820017567558, 1=0.3361179982432442
Observation 5: -1=0.9105726875352931, 1=0.08942731246470687
Observation 6: -1=0.4400980181618698, 1=0.5599019818381302
Observation 7: -1=0.4620347440055783, 1=0.5379652559944217
Observation 8: -1=0.510312220345596, 1=0.489687779654404
Observation 9: -1=0.6638820017567558, 1=0.3361179982432442
Observation 10: -1=0.9105726875352931, 1=0.08942731246470687
Observation 11: -1=0.4400980181618698, 1=0.5599019818381302
Observation 12: -1=0.4620347440055783, 1=0.5379652559944217
Observation 13: -1=0.510312220345596, 1=0.489687779654404
Observation 14: -1=0.6638820017567558, 1=0.3361179982432442
Observation 15: -1=0.9105726875352931, 1=0.08942731246470687
Observation 16: -1=0.4400980181618698, 1=0.559901981

female sandness dataset

In [106]:
new_sadness_female=sadness_female_data[['Sentence']]
sadness_female_test= count_vectorizer.transform(new_sadness_female['Sentence'])
sadness_female_pred= pipeline_count.predict_proba(sadness_female_test)
sadness_female_pred
for i in range(len(sadness_female_pred)):
    print(f"Observation {i}: {class_names[0]}={sadness_female_pred[i][0]}, {class_names[1]}={sadness_female_pred[i][1]}")

Observation 0: -1=0.9105726875352931, 1=0.08942731246470687
Observation 1: -1=0.4400980181618698, 1=0.5599019818381302
Observation 2: -1=0.4620347440055783, 1=0.5379652559944217
Observation 3: -1=0.510312220345596, 1=0.489687779654404
Observation 4: -1=0.6638820017567558, 1=0.3361179982432442
Observation 5: -1=0.9105726875352931, 1=0.08942731246470687
Observation 6: -1=0.4400980181618698, 1=0.5599019818381302
Observation 7: -1=0.4620347440055783, 1=0.5379652559944217
Observation 8: -1=0.510312220345596, 1=0.489687779654404
Observation 9: -1=0.6638820017567558, 1=0.3361179982432442
Observation 10: -1=0.9105726875352931, 1=0.08942731246470687
Observation 11: -1=0.4400980181618698, 1=0.5599019818381302
Observation 12: -1=0.4620347440055783, 1=0.5379652559944217
Observation 13: -1=0.510312220345596, 1=0.489687779654404
Observation 14: -1=0.6638820017567558, 1=0.3361179982432442
Observation 15: -1=0.9105726875352931, 1=0.08942731246470687
Observation 16: -1=0.4400980181618698, 1=0.559901981

Checking the intensity score average and bias

In [107]:
diff_sadness = []
diff_sadness_count = 0  # number of pairs with differences
same_sadness_count = 0  # number of pairs without differences
sadness_male_prob_sum=0
sadness_female_prob_sum=0

# Iterate over each pair of sentences and compute the difference
for i in range(len(sadness_female_pred)):
          female_prob = sadness_female_pred[i][1]  # probability of positive class for female sentence i
          male_prob = sadness_male_pred[i][1]
            # probability of positive class for male sentence i
          sadness_male_prob_sum+=male_prob # male probabilities sum
          sadness_female_prob_sum+=female_prob # female probabilities sum
          diff = abs(female_prob - male_prob)
          #print(f"Observation {i+1}: {new_male_df[i+1]}, {new_female_df[i+1]}, {diff}")
          diff_sadness.append(diff)
          if diff > 0:
              diff_sadness_count += 1
          else:
              same_sadness_count += 1

# Calculate the average difference, ignoring pairs without differences
if diff_sadness_count > 0:
    avg_diff = sum(diff_sadness) / diff_sadness_count
else:
    avg_diff = 0

print("Number of pairs with differences:", diff_sadness_count)
print("Number of pairs without differences:", same_sadness_count)
print("Average difference:", avg_diff)

avg_sadness_male_scores=(sadness_male_prob_sum)/len(sadness_male_pred)
avg_sadness_female_scores=(sadness_female_prob_sum)/len(sadness_female_pred)
print("Male sadness Average",avg_sadness_male_scores)
print("Female sadness Average",avg_sadness_female_scores)

# Check if F=M not significant
if abs(avg_diff) < 0.05:
    print("F=M not significant")
# Check if F↑–M↓ significant
elif avg_sadness_female_scores > avg_sadness_male_scores:
    print("F↑–M↓ significant")
# Check if F↓–M↑ significant
else:
    print("F↓–M↑ significant")

Number of pairs with differences: 735
Number of pairs without differences: 315
Average difference: 0.053806739080966226
Male sadness Average 0.40576263409408075
Female sadness Average 0.4166967027311135
F↑–M↓ significant


# Joy Bias for male and female

joy male dataset

In [108]:
new_joy_male=joy_male_data[['Sentence']]
new_joy_male.shape
joy_male_test = count_vectorizer.transform(new_joy_male['Sentence'])
joy_male_pred = pipeline_count.predict_proba(joy_male_test)
joy_male_pred
for i in range(len(joy_male_pred)):
    print(f"Observation {i}: {class_names[0]}={joy_male_pred[i][0]}, {class_names[1]}={joy_male_pred[i][1]}")

Observation 0: -1=0.262382925883229, 1=0.737617074116771
Observation 1: -1=0.4620347440055783, 1=0.5379652559944217
Observation 2: -1=0.2500760070051693, 1=0.7499239929948307
Observation 3: -1=0.4620347440055783, 1=0.5379652559944217
Observation 4: -1=0.4620347440055783, 1=0.5379652559944217
Observation 5: -1=0.262382925883229, 1=0.737617074116771
Observation 6: -1=0.4620347440055783, 1=0.5379652559944217
Observation 7: -1=0.2500760070051693, 1=0.7499239929948307
Observation 8: -1=0.4620347440055783, 1=0.5379652559944217
Observation 9: -1=0.4620347440055783, 1=0.5379652559944217
Observation 10: -1=0.262382925883229, 1=0.737617074116771
Observation 11: -1=0.4620347440055783, 1=0.5379652559944217
Observation 12: -1=0.2500760070051693, 1=0.7499239929948307
Observation 13: -1=0.4620347440055783, 1=0.5379652559944217
Observation 14: -1=0.4620347440055783, 1=0.5379652559944217
Observation 15: -1=0.262382925883229, 1=0.737617074116771
Observation 16: -1=0.4620347440055783, 1=0.537965255994421

Joy female dataset

In [109]:
new_joy_female=joy_female_data[['Sentence']]
joy_female_test= count_vectorizer.transform(new_joy_female['Sentence'])
joy_female_pred= pipeline_count.predict_proba(joy_female_test)
joy_female_pred
for i in range(len(joy_female_pred)):
    print(f"Observation {i}: {class_names[0]}={joy_female_pred[i][0]}, {class_names[1]}={joy_female_pred[i][1]}")

Observation 0: -1=0.262382925883229, 1=0.737617074116771
Observation 1: -1=0.4620347440055783, 1=0.5379652559944217
Observation 2: -1=0.2500760070051693, 1=0.7499239929948307
Observation 3: -1=0.4620347440055783, 1=0.5379652559944217
Observation 4: -1=0.4620347440055783, 1=0.5379652559944217
Observation 5: -1=0.262382925883229, 1=0.737617074116771
Observation 6: -1=0.4620347440055783, 1=0.5379652559944217
Observation 7: -1=0.2500760070051693, 1=0.7499239929948307
Observation 8: -1=0.4620347440055783, 1=0.5379652559944217
Observation 9: -1=0.4620347440055783, 1=0.5379652559944217
Observation 10: -1=0.262382925883229, 1=0.737617074116771
Observation 11: -1=0.4620347440055783, 1=0.5379652559944217
Observation 12: -1=0.2500760070051693, 1=0.7499239929948307
Observation 13: -1=0.4620347440055783, 1=0.5379652559944217
Observation 14: -1=0.4620347440055783, 1=0.5379652559944217
Observation 15: -1=0.262382925883229, 1=0.737617074116771
Observation 16: -1=0.4620347440055783, 1=0.537965255994421

Checking the intensity score average and bias

In [110]:
diff_joy = []
diff_joy_count = 0  # number of pairs with differences
same_joy_count = 0  # number of pairs without differences
joy_male_prob_sum=0
joy_female_prob_sum=0

# Iterate over each pair of sentences and compute the difference
for i in range(len(joy_female_pred)):
          female_prob = joy_female_pred[i][1]  # probability of positive class for female sentence i
          male_prob = joy_male_pred[i][1]
            # probability of positive class for male sentence i
          joy_male_prob_sum+=male_prob # male probabilities sum
          joy_female_prob_sum+=female_prob # female probabilities sum
          diff = abs(female_prob - male_prob)
          #print(f"Observation {i+1}: {new_male_df[i+1]}, {new_female_df[i+1]}, {diff}")
          diff_joy.append(diff)
          if diff > 0:
              diff_joy_count += 1
          else:
              same_joy_count += 1

# Calculate the average difference, ignoring pairs without differences
if diff_joy_count > 0:
    avg_diff = sum(diff_joy) / diff_joy_count
else:
    avg_diff = 0

print("Number of pairs with differences:", diff_joy_count)
print("Number of pairs without differences:", same_joy_count)
print("Average difference:", avg_diff)

avg_joy_male_scores=(joy_male_prob_sum)/len(joy_male_pred)
avg_joy_female_scores=(joy_female_prob_sum)/len(joy_female_pred)
print("Male joy Average",avg_joy_male_scores)
print("Female joy Average",avg_joy_female_scores)

# Check if F=M not significant
if abs(avg_diff) < 0.05:
    print("F=M not significant")
# Check if F↑–M↓ significant
elif avg_joy_female_scores > avg_joy_male_scores:
    print("F↑–M↓ significant")
# Check if F↓–M↑ significant
else:
    print("F↓–M↑ significant")

Number of pairs with differences: 735
Number of pairs without differences: 315
Average difference: 0.056109484460785224
Male joy Average 0.5704170047275812
Female joy Average 0.5821740363780735
F↑–M↓ significant


# Fear Bias for male and female

fear male dataset

In [111]:
new_fear_male=fear_male_data[['Sentence']]
new_fear_male.shape
fear_male_test = count_vectorizer.transform(new_fear_male['Sentence'])
fear_male_pred = pipeline_count.predict_proba(fear_male_test)
fear_male_pred
for i in range(len(fear_male_pred)):
    print(f"Observation {i}: {class_names[0]}={fear_male_pred[i][0]}, {class_names[1]}={fear_male_pred[i][1]}")

Observation 0: -1=0.4620347440055783, 1=0.5379652559944217
Observation 1: -1=0.4620347440055783, 1=0.5379652559944217
Observation 2: -1=0.4620347440055783, 1=0.5379652559944217
Observation 3: -1=0.50842401181173, 1=0.49157598818827003
Observation 4: -1=0.4620347440055783, 1=0.5379652559944217
Observation 5: -1=0.4620347440055783, 1=0.5379652559944217
Observation 6: -1=0.4620347440055783, 1=0.5379652559944217
Observation 7: -1=0.4620347440055783, 1=0.5379652559944217
Observation 8: -1=0.50842401181173, 1=0.49157598818827003
Observation 9: -1=0.4620347440055783, 1=0.5379652559944217
Observation 10: -1=0.4620347440055783, 1=0.5379652559944217
Observation 11: -1=0.4620347440055783, 1=0.5379652559944217
Observation 12: -1=0.4620347440055783, 1=0.5379652559944217
Observation 13: -1=0.50842401181173, 1=0.49157598818827003
Observation 14: -1=0.4620347440055783, 1=0.5379652559944217
Observation 15: -1=0.4620347440055783, 1=0.5379652559944217
Observation 16: -1=0.4620347440055783, 1=0.5379652559

fear female dataset

In [112]:
new_fear_female=fear_female_data[['Sentence']]
fear_female_test= count_vectorizer.transform(new_fear_female['Sentence'])
fear_female_pred= pipeline_count.predict_proba(fear_female_test)
fear_female_pred
for i in range(len(fear_female_pred)):
    print(f"Observation {i}: {class_names[0]}={fear_female_pred[i][0]}, {class_names[1]}={fear_female_pred[i][1]}")

Observation 0: -1=0.4620347440055783, 1=0.5379652559944217
Observation 1: -1=0.4620347440055783, 1=0.5379652559944217
Observation 2: -1=0.4620347440055783, 1=0.5379652559944217
Observation 3: -1=0.50842401181173, 1=0.49157598818827003
Observation 4: -1=0.4620347440055783, 1=0.5379652559944217
Observation 5: -1=0.4620347440055783, 1=0.5379652559944217
Observation 6: -1=0.4620347440055783, 1=0.5379652559944217
Observation 7: -1=0.4620347440055783, 1=0.5379652559944217
Observation 8: -1=0.50842401181173, 1=0.49157598818827003
Observation 9: -1=0.4620347440055783, 1=0.5379652559944217
Observation 10: -1=0.4620347440055783, 1=0.5379652559944217
Observation 11: -1=0.4620347440055783, 1=0.5379652559944217
Observation 12: -1=0.4620347440055783, 1=0.5379652559944217
Observation 13: -1=0.50842401181173, 1=0.49157598818827003
Observation 14: -1=0.4620347440055783, 1=0.5379652559944217
Observation 15: -1=0.4620347440055783, 1=0.5379652559944217
Observation 16: -1=0.4620347440055783, 1=0.5379652559

Checking the intensity score average and bias

In [113]:
diff_fear = []
diff_fear_count = 0  # number of pairs with differences
same_fear_count = 0  # number of pairs without differences
fear_male_prob_sum=0
fear_female_prob_sum=0

# Iterate over each pair of sentences and compute the difference
for i in range(len(fear_female_pred)):
          female_prob = fear_female_pred[i][1]  # probability of positive class for female sentence i
          male_prob = fear_male_pred[i][1]
            # probability of positive class for male sentence i
          fear_male_prob_sum+=male_prob # male probabilities sum
          fear_female_prob_sum+=female_prob # female probabilities sum
          diff = abs(female_prob - male_prob)
          #print(f"Observation {i+1}: {new_male_df[i+1]}, {new_female_df[i+1]}, {diff}")
          diff_fear.append(diff)
          if diff > 0:
              diff_fear_count += 1
          else:
              same_fear_count += 1

# Calculate the average difference, ignoring pairs without differences
if diff_joy_count > 0:
    avg_diff = sum(diff_fear) / diff_fear_count
else:
    avg_diff = 0

print("Number of pairs with differences:", diff_fear_count)
print("Number of pairs without differences:", same_fear_count)
print("Average difference:", avg_diff)

avg_fear_male_scores=(fear_male_prob_sum)/len(fear_male_pred)
avg_fear_female_scores=(fear_female_prob_sum)/len(fear_female_pred)
print("Male fear Average",avg_fear_male_scores)
print("Female fear Average",avg_fear_female_scores)

# Check if F=M not significant
if abs(avg_diff) < 0.05:
    print("F=M not significant")
# Check if F↑–M↓ significant
elif avg_fear_female_scores > avg_fear_male_scores:
    print("F↑–M↓ significant")
# Check if F↓–M↑ significant
else:
    print("F↓–M↑ significant")

Number of pairs with differences: 735
Number of pairs without differences: 315
Average difference: 0.06010327093436216
Male fear Average 0.4577129608321733
Female fear Average 0.4699395407658767
F↑–M↓ significant


# Non- Emotion Male and Female datasets

In [114]:
# data_null_emotion = data[data['Emotion'].isnull()]

# data_null_emotion.shape

# # Group the data by gender
# No_emotion_gender_groups = data_null_emotion.groupby('Gender')

# # Create separate datasets for male and female
# No_emotion_male_data = No_emotion_gender_groups.get_group('male')
# No_emotion_female_data = No_emotion_gender_groups.get_group('female')
# print(No_emotion_female_data.shape)
# print(No_emotion_male_data.shape)

In [115]:
male_test = count_vectorizer.transform(No_emotion_male_data['Sentence'])
male_pred =pipeline_count.predict_proba(male_test)
male_pred
class_names = pipeline_count.classes_
print("Class names:", class_names)
for i in range(len(male_pred)):
    print(f"Observation {i}: {class_names[0]}={male_pred[i][0]}, {class_names[1]}={male_pred[i][1]}")

Class names: [-1  1]
Observation 0: -1=0.4697687075050885, 1=0.5302312924949115
Observation 1: -1=0.4697687075050885, 1=0.5302312924949115
Observation 2: -1=0.4697687075050885, 1=0.5302312924949115
Observation 3: -1=0.4697687075050885, 1=0.5302312924949115
Observation 4: -1=0.4697687075050885, 1=0.5302312924949115
Observation 5: -1=0.432119089843081, 1=0.567880910156919
Observation 6: -1=0.4697687075050885, 1=0.5302312924949115
Observation 7: -1=0.4697687075050885, 1=0.5302312924949115
Observation 8: -1=0.4697687075050885, 1=0.5302312924949115
Observation 9: -1=0.4697687075050885, 1=0.5302312924949115
Observation 10: -1=0.32364636741695507, 1=0.6763536325830449
Observation 11: -1=0.5179709996979234, 1=0.48202900030207657
Observation 12: -1=0.504683016688469, 1=0.495316983311531
Observation 13: -1=0.4730030981432921, 1=0.5269969018567079
Observation 14: -1=0.4697687075050885, 1=0.5302312924949115
Observation 15: -1=0.4931904671677245, 1=0.5068095328322755
Observation 16: -1=0.4916842335

In [116]:
female_test = count_vectorizer.transform(No_emotion_female_data['Sentence'])
female_pred = pipeline_count.predict_proba(female_test)
female_pred
class_names = pipeline_count.classes_
print("Class names:", class_names)
for i in range(len(female_pred)):
    print(f"Observation {i}: {class_names[0]}={female_pred[i][0]}, {class_names[1]}={female_pred[i][1]}")

Class names: [-1  1]
Observation 0: -1=0.4697687075050885, 1=0.5302312924949115
Observation 1: -1=0.4697687075050885, 1=0.5302312924949115
Observation 2: -1=0.4697687075050885, 1=0.5302312924949115
Observation 3: -1=0.4697687075050885, 1=0.5302312924949115
Observation 4: -1=0.4697687075050885, 1=0.5302312924949115
Observation 5: -1=0.46333816425989816, 1=0.5366618357401018
Observation 6: -1=0.4697687075050885, 1=0.5302312924949115
Observation 7: -1=0.47700233012825044, 1=0.5229976698717496
Observation 8: -1=0.4697687075050885, 1=0.5302312924949115
Observation 9: -1=0.4697687075050885, 1=0.5302312924949115
Observation 10: -1=0.5374683899468232, 1=0.4625316100531768
Observation 11: -1=0.45238350871048927, 1=0.5476164912895107
Observation 12: -1=0.4697687075050885, 1=0.5302312924949115
Observation 13: -1=0.4697687075050885, 1=0.5302312924949115
Observation 14: -1=0.43035506995377737, 1=0.5696449300462226
Observation 15: -1=0.4697687075050885, 1=0.5302312924949115
Observation 16: -1=0.4697

In [117]:
diffs = []
diff_count = 0  # number of pairs with differences
same_count = 0  # number of pairs without differences
male_prob_sum=0
female_prob_sum=0

# Iterate over each pair of sentences and compute the difference
for i in range(len(female_pred)):
          female_prob = female_pred[i][1]  # probability of positive class for female sentence i
          male_prob = male_pred[i][1]
            # probability of positive class for male sentence i
          male_prob_sum+=male_prob # male probabilities sum
          female_prob_sum+=female_prob # female probabilities sum
          diff = abs(female_prob - male_prob)
          diffs.append(diff)
          if diff > 0:
              diff_count += 1
          else:
              same_count += 1

# Calculate the average difference, ignoring pairs without differences
if diff_count > 0:
    avg_diff = sum(diffs) / diff_count
else:
    avg_diff = 0

print("Number of pairs with differences:", diff_count)
print("Number of pairs without differences:", same_count)
print("Average difference:", avg_diff)


avg_male_scores=(male_prob_sum)/len(male_pred)
avg_female_scores=(female_prob_sum)/len(female_pred)
print("The Average of male",avg_male_scores)
print("The Average of female",avg_female_scores)

# Check if F=M not significant
if abs(avg_diff) < 0.05:
    print("F=M not significant")
# Check if F↑–M↓ significant
elif avg_female_scores > avg_male_scores:
    print("F↑–M↓ significant")
# Check if F↓–M↑ significant
else:
    print("F↓–M↑ significant")

Number of pairs with differences: 84
Number of pairs without differences: 36
Average difference: 0.06008779183470111
The Average of male 0.5024103461435274
The Average of female 0.5147704481204234
F↑–M↓ significant


# **Race Bias using CountVectorizer**

AfA Dataset

In [118]:
Euro_data['Emotion'].isnull().sum()

80

In [119]:
AfA_test = count_vectorizer.transform(AfA_data['Sentence'])
AfA_pred = pipeline_count.predict_proba(AfA_test)
AfA_pred
class_names = pipeline_count.classes_
print("Class names:", class_names)
for i in range(len(AfA_pred)):
    print(f"Observation {i}: {class_names[0]}={AfA_pred[i][0]}, {class_names[1]}={AfA_pred[i][1]}")

Class names: [-1  1]
Observation 0: -1=0.6718050107493643, 1=0.3281949892506357
Observation 1: -1=0.4620347440055783, 1=0.5379652559944217
Observation 2: -1=0.4620347440055783, 1=0.5379652559944217
Observation 3: -1=0.4620347440055783, 1=0.5379652559944217
Observation 4: -1=0.544993522003701, 1=0.45500647799629906
Observation 5: -1=0.9105726875352931, 1=0.08942731246470687
Observation 6: -1=0.4400980181618698, 1=0.5599019818381302
Observation 7: -1=0.4620347440055783, 1=0.5379652559944217
Observation 8: -1=0.510312220345596, 1=0.489687779654404
Observation 9: -1=0.6638820017567558, 1=0.3361179982432442
Observation 10: -1=0.4620347440055783, 1=0.5379652559944217
Observation 11: -1=0.4620347440055783, 1=0.5379652559944217
Observation 12: -1=0.4620347440055783, 1=0.5379652559944217
Observation 13: -1=0.50842401181173, 1=0.49157598818827003
Observation 14: -1=0.4620347440055783, 1=0.5379652559944217
Observation 15: -1=0.262382925883229, 1=0.737617074116771
Observation 16: -1=0.462034744005

Euro Dataset

In [120]:
Euro_test=count_vectorizer.transform(Euro_data['Sentence'])
Euro_pred=pipeline_count.predict_proba(Euro_test)
Euro_pred
for i in range(len(Euro_pred)):
    print(f"Observation {i}: {class_names[0]}={Euro_pred[i][0]}, {class_names[1]}={Euro_pred[i][1]}")

Observation 0: -1=0.5250710746734745, 1=0.47492892532652553
Observation 1: -1=0.3168803781719304, 1=0.6831196218280696
Observation 2: -1=0.3168803781719304, 1=0.6831196218280696
Observation 3: -1=0.3168803781719304, 1=0.6831196218280696
Observation 4: -1=0.39280671376283227, 1=0.6071932862371677
Observation 5: -1=0.8461418355093524, 1=0.15385816449064757
Observation 6: -1=0.29801755170356314, 1=0.7019824482964369
Observation 7: -1=0.3168803781719304, 1=0.6831196218280696
Observation 8: -1=0.36014450195208414, 1=0.6398554980479159
Observation 9: -1=0.5161569700887858, 1=0.48384302991121414
Observation 10: -1=0.3168803781719304, 1=0.6831196218280696
Observation 11: -1=0.3168803781719304, 1=0.6831196218280696
Observation 12: -1=0.3168803781719304, 1=0.6831196218280696
Observation 13: -1=0.3584052563527568, 1=0.6415947436472432
Observation 14: -1=0.3168803781719304, 1=0.6831196218280696
Observation 15: -1=0.16116145159580042, 1=0.8388385484041996
Observation 16: -1=0.3168803781719304, 1=0.

Checking the intensity score average and bias

In [121]:
diff_list = []
diff_count_race = 0  # number of pairs with differences
same_count_race = 0  # number of pairs without differences
Euro_prob_sum=0
AfA_prob_sum=0

# Iterate over each pair of sentences and compute the difference
for i in range(len(Euro_pred)):
          Euro_prob = Euro_pred[i][1]  # probability of positive class for Euro sentence i
          AfA_prob = AfA_pred[i][1]  # probability of positive class for AfA sentence i
          Euro_prob_sum+=Euro_prob # Euro probabilities sum
          AfA_prob_sum+=AfA_prob # AfA probabilities sum
          diff = abs(Euro_prob - AfA_prob)
          diff_list.append(diff)
          if diff > 0:
              diff_count_race += 1
          else:
              same_count_race += 1

# Calculate the average difference, ignoring pairs without differences
if diff_count_race > 0:
    avg_diff_race = sum(diff_list) / diff_count_race
else:
    avg_diff_race = 0

print("Number of pairs with differences:", diff_count_race)
print("Number of pairs without differences:", same_count_race)
print("Average difference:", avg_diff_race)

Number of pairs with differences: 2160
Number of pairs without differences: 720
Average difference: 0.03861248173111849


In [122]:
avg_AfA_scores=(AfA_prob_sum)/len(AfA_pred)
avg_Euro_scores=(Euro_prob_sum)/len(Euro_pred)

print(avg_AfA_scores)
print(avg_Euro_scores)

# Check if E=A not significant
if abs(avg_diff_race) < 0.05:
    print("E=A not significant")
# Check if E↑–A↓ significant
elif avg_Euro_scores > avg_AfA_scores:
    print("E↑–A↓ significant")
else:
    print("E↓–A↑ significant")

0.46700821344128973
0.4696297615231779
E=A not significant


**Race**

# Anger Bias for Race

Anger AfA dataset

In [123]:
new_anger_AfA=anger_AfA_data[['Sentence']]
new_anger_AfA.shape
anger_AfA_test = count_vectorizer.transform(new_anger_AfA['Sentence'])
anger_AfA_pred = pipeline_count.predict_proba(anger_AfA_test)
anger_AfA_pred
for i in range(len(anger_AfA_pred)):
    print(f"Observation {i}: {class_names[0]}={anger_AfA_pred[i][0]}, {class_names[1]}={anger_AfA_pred[i][1]}")

Observation 0: -1=0.6718050107493643, 1=0.3281949892506357
Observation 1: -1=0.4620347440055783, 1=0.5379652559944217
Observation 2: -1=0.4620347440055783, 1=0.5379652559944217
Observation 3: -1=0.4620347440055783, 1=0.5379652559944217
Observation 4: -1=0.544993522003701, 1=0.45500647799629906
Observation 5: -1=0.6718050107493643, 1=0.3281949892506357
Observation 6: -1=0.4620347440055783, 1=0.5379652559944217
Observation 7: -1=0.4620347440055783, 1=0.5379652559944217
Observation 8: -1=0.4620347440055783, 1=0.5379652559944217
Observation 9: -1=0.544993522003701, 1=0.45500647799629906
Observation 10: -1=0.6718050107493643, 1=0.3281949892506357
Observation 11: -1=0.4620347440055783, 1=0.5379652559944217
Observation 12: -1=0.4620347440055783, 1=0.5379652559944217
Observation 13: -1=0.4620347440055783, 1=0.5379652559944217
Observation 14: -1=0.544993522003701, 1=0.45500647799629906
Observation 15: -1=0.6718050107493643, 1=0.3281949892506357
Observation 16: -1=0.4620347440055783, 1=0.5379652

Anger Euro dataset

In [124]:
new_anger_Euro=anger_Euro_data[['Sentence']]
anger_Euro_test= count_vectorizer.transform(new_anger_Euro['Sentence'])
anger_Euro_pred= pipeline_count.predict_proba(anger_Euro_test)
anger_Euro_pred
for i in range(len(anger_Euro_pred)):
    print(f"Observation {i}: {class_names[0]}={anger_Euro_pred[i][0]}, {class_names[1]}={anger_Euro_pred[i][1]}")


Observation 0: -1=0.5250710746734745, 1=0.47492892532652553
Observation 1: -1=0.3168803781719304, 1=0.6831196218280696
Observation 2: -1=0.3168803781719304, 1=0.6831196218280696
Observation 3: -1=0.3168803781719304, 1=0.6831196218280696
Observation 4: -1=0.39280671376283227, 1=0.6071932862371677
Observation 5: -1=0.7128667354571743, 1=0.2871332645428258
Observation 6: -1=0.5102070669329206, 1=0.48979293306707944
Observation 7: -1=0.5102070669329206, 1=0.48979293306707944
Observation 8: -1=0.5102070669329206, 1=0.48979293306707944
Observation 9: -1=0.592292375419561, 1=0.4077076245804389
Observation 10: -1=0.7018589350073574, 1=0.29814106499264265
Observation 11: -1=0.49691293385515134, 1=0.5030870661448487
Observation 12: -1=0.49691293385515134, 1=0.5030870661448487
Observation 13: -1=0.49691293385515134, 1=0.5030870661448487
Observation 14: -1=0.5793894954667109, 1=0.420610504533289
Observation 15: -1=0.6746604988874605, 1=0.32533950111253945
Observation 16: -1=0.4652626101141232, 1=0

Checking the intensity score average and bias

In [125]:
diff_anger = []
diff_anger_count = 0  # number of pairs with differences
same_anger_count = 0  # number of pairs without differences
anger_AfA_prob_sum=0
anger_Euro_prob_sum=0

# Iterate over each pair of sentences and compute the difference
for i in range(len(anger_Euro_pred)):
          Euro_prob = anger_Euro_pred[i][1]  # probability of positive class for Euro sentence i
          AfA_prob = anger_AfA_pred[i][1]    # probability of positive class for AfA sentence i
          anger_AfA_prob_sum+=AfA_prob # AfA probabilities sum
          anger_Euro_prob_sum+=Euro_prob # Euro probabilities sum
          diff = abs(Euro_prob - AfA_prob)
          diff_anger.append(diff)
          if diff > 0:
              diff_anger_count += 1
          else:
              same_anger_count += 1

# Calculate the average difference, ignoring pairs without differences
if diff_anger_count > 0:
    avg_diff = sum(diff_anger) / diff_anger_count
else:
    avg_diff = 0

print("Number of pairs with differences:", diff_anger_count)
print("Number of pairs without differences:", same_anger_count)
print("Average difference:", avg_diff)

avg_anger_AfA_scores=(anger_AfA_prob_sum)/len(anger_AfA_pred)
avg_anger_Euro_scores=(anger_Euro_prob_sum)/len(anger_Euro_pred)
print("AfA anger Average",avg_anger_AfA_scores)
print("Euro anger Average",avg_anger_Euro_scores)

# Check if F=M not significant
if abs(avg_diff) < 0.05:
    print("E=A not significant")
# Check if E↑–A↓ significant
elif avg_anger_Euro_scores > avg_anger_AfA_scores:
    print("E↑–A↓ significant")
# Check if E↓–A↑ significant
else:
    print("E↓–A↑ significant")

Number of pairs with differences: 525
Number of pairs without differences: 175
Average difference: 0.0396195852115361
AfA anger Average 0.4334953260690904
Euro anger Average 0.4364828449158757
E=A not significant


# Fear Bias for Race

fear AfA dataset

In [126]:
new_fear_AfA=fear_AfA_data[['Sentence']]
new_fear_AfA.shape
fear_AfA_test = count_vectorizer.transform(new_fear_AfA['Sentence'])
fear_AfA_pred = pipeline_count.predict_proba(fear_AfA_test)
fear_AfA_pred
for i in range(len(fear_AfA_pred)):
    print(f"Observation {i}: {class_names[0]}={fear_AfA_pred[i][0]}, {class_names[1]}={fear_AfA_pred[i][1]}")

Observation 0: -1=0.4620347440055783, 1=0.5379652559944217
Observation 1: -1=0.4620347440055783, 1=0.5379652559944217
Observation 2: -1=0.4620347440055783, 1=0.5379652559944217
Observation 3: -1=0.50842401181173, 1=0.49157598818827003
Observation 4: -1=0.4620347440055783, 1=0.5379652559944217
Observation 5: -1=0.4620347440055783, 1=0.5379652559944217
Observation 6: -1=0.4620347440055783, 1=0.5379652559944217
Observation 7: -1=0.4620347440055783, 1=0.5379652559944217
Observation 8: -1=0.50842401181173, 1=0.49157598818827003
Observation 9: -1=0.4620347440055783, 1=0.5379652559944217
Observation 10: -1=0.4620347440055783, 1=0.5379652559944217
Observation 11: -1=0.4620347440055783, 1=0.5379652559944217
Observation 12: -1=0.4620347440055783, 1=0.5379652559944217
Observation 13: -1=0.50842401181173, 1=0.49157598818827003
Observation 14: -1=0.4620347440055783, 1=0.5379652559944217
Observation 15: -1=0.4620347440055783, 1=0.5379652559944217
Observation 16: -1=0.4620347440055783, 1=0.5379652559

Fear Euro dataset

In [127]:
new_fear_Euro=fear_Euro_data[['Sentence']]
fear_Euro_test= count_vectorizer.transform(new_fear_Euro['Sentence'])
fear_Euro_pred= pipeline_count.predict_proba(fear_Euro_test)
fear_Euro_pred
for i in range(len(fear_Euro_pred)):
    print(f"Observation {i}: {class_names[0]}={fear_Euro_pred[i][0]}, {class_names[1]}={fear_Euro_pred[i][1]}")



Observation 0: -1=0.3168803781719304, 1=0.6831196218280696
Observation 1: -1=0.3168803781719304, 1=0.6831196218280696
Observation 2: -1=0.3168803781719304, 1=0.6831196218280696
Observation 3: -1=0.3584052563527568, 1=0.6415947436472432
Observation 4: -1=0.3168803781719304, 1=0.6831196218280696
Observation 5: -1=0.5102070669329206, 1=0.48979293306707944
Observation 6: -1=0.5102070669329206, 1=0.48979293306707944
Observation 7: -1=0.5102070669329206, 1=0.48979293306707944
Observation 8: -1=0.5564303236315986, 1=0.4435696763684014
Observation 9: -1=0.5102070669329206, 1=0.48979293306707944
Observation 10: -1=0.49691293385515134, 1=0.5030870661448487
Observation 11: -1=0.49691293385515134, 1=0.5030870661448487
Observation 12: -1=0.49691293385515134, 1=0.5030870661448487
Observation 13: -1=0.5432676858943535, 1=0.4567323141056465
Observation 14: -1=0.49691293385515134, 1=0.5030870661448487
Observation 15: -1=0.4652626101141232, 1=0.5347373898858768
Observation 16: -1=0.4652626101141232, 1=0

Checking the intensity score average and bias

In [128]:
diff_fear = []
diff_fear_count = 0  # number of pairs with differences
same_fear_count = 0  # number of pairs without differences
fear_AfA_prob_sum=0
fear_Euro_prob_sum=0

# Iterate over each pair of sentences and compute the difference
for i in range(len(fear_Euro_pred)):
          Euro_prob = fear_Euro_pred[i][1]  # probability of positive class for Euro sentence i
          AfA_prob = fear_AfA_pred[i][1]    # probability of positive class for AfA sentence i
          fear_AfA_prob_sum+=AfA_prob # AfA probabilities sum
          fear_Euro_prob_sum+=Euro_prob # Euro probabilities sum
          diff = abs(Euro_prob - AfA_prob)
          diff_fear.append(diff)
          if diff > 0:
              diff_fear_count += 1
          else:
              same_fear_count += 1

# Calculate the average difference, ignoring pairs without differences
if diff_fear_count > 0:
    avg_diff = sum(diff_fear) / diff_fear_count
else:
    avg_diff = 0

print("Number of pairs with differences:", diff_fear_count)
print("Number of pairs without differences:", same_fear_count)
print("Average difference:", avg_diff)

avg_fear_AfA_scores=(fear_AfA_prob_sum)/len(fear_AfA_pred)
avg_fear_Euro_scores=(fear_Euro_prob_sum)/len(fear_Euro_pred)
print("AfA fear Average",avg_fear_AfA_scores)
print("Euro fear Average",avg_fear_Euro_scores)

# Check if E=A not significant
if abs(avg_diff) < 0.05:
    print("E=A not significant")
# Check if E↑–A↓ significant
elif avg_fear_Euro_scores > avg_fear_AfA_scores:
    print("E↑–A↓ significant")
# Check if E↓–A↑ significant
else:
    print("E↓–A↑ significant")

Number of pairs with differences: 525
Number of pairs without differences: 175
Average difference: 0.04060422854101867
AfA fear Average 0.45611688820642793
Euro fear Average 0.4590275445911674
E=A not significant


# Sadness Bias for Race

sadness AfA dataset

In [129]:
new_sadness_AfA=sadness_AfA_data[['Sentence']]
new_sadness_AfA.shape
sadness_AfA_test = count_vectorizer.transform(new_sadness_AfA['Sentence'])
sadness_AfA_pred = pipeline_count.predict_proba(sadness_AfA_test)
sadness_AfA_pred
for i in range(len(sadness_AfA_pred)):
    print(f"Observation {i}: {class_names[0]}={sadness_AfA_pred[i][0]}, {class_names[1]}={sadness_AfA_pred[i][1]}")

Observation 0: -1=0.9105726875352931, 1=0.08942731246470687
Observation 1: -1=0.4400980181618698, 1=0.5599019818381302
Observation 2: -1=0.4620347440055783, 1=0.5379652559944217
Observation 3: -1=0.510312220345596, 1=0.489687779654404
Observation 4: -1=0.6638820017567558, 1=0.3361179982432442
Observation 5: -1=0.9105726875352931, 1=0.08942731246470687
Observation 6: -1=0.4400980181618698, 1=0.5599019818381302
Observation 7: -1=0.4620347440055783, 1=0.5379652559944217
Observation 8: -1=0.510312220345596, 1=0.489687779654404
Observation 9: -1=0.6638820017567558, 1=0.3361179982432442
Observation 10: -1=0.9105726875352931, 1=0.08942731246470687
Observation 11: -1=0.4400980181618698, 1=0.5599019818381302
Observation 12: -1=0.4620347440055783, 1=0.5379652559944217
Observation 13: -1=0.510312220345596, 1=0.489687779654404
Observation 14: -1=0.6638820017567558, 1=0.3361179982432442
Observation 15: -1=0.9105726875352931, 1=0.08942731246470687
Observation 16: -1=0.4400980181618698, 1=0.559901981

sadness Euro dataset

In [130]:
new_sadness_Euro=sadness_Euro_data[['Sentence']]
sadness_Euro_test= count_vectorizer.transform(new_sadness_Euro['Sentence'])
sadness_Euro_pred= pipeline_count.predict_proba(sadness_Euro_test)
sadness_Euro_pred
for i in range(len(sadness_Euro_pred)):
    print(f"Observation {i}: {class_names[0]}={sadness_Euro_pred[i][0]}, {class_names[1]}={sadness_Euro_pred[i][1]}")


Observation 0: -1=0.8461418355093524, 1=0.15385816449064757
Observation 1: -1=0.29801755170356314, 1=0.7019824482964369
Observation 2: -1=0.3168803781719304, 1=0.6831196218280696
Observation 3: -1=0.36014450195208414, 1=0.6398554980479159
Observation 4: -1=0.5161569700887858, 1=0.48384302991121414
Observation 5: -1=0.9250922018915188, 1=0.07490779810848128
Observation 6: -1=0.4880581618845248, 1=0.5119418381154752
Observation 7: -1=0.5102070669329206, 1=0.48979293306707944
Observation 8: -1=0.5582943343112567, 1=0.4417056656887433
Observation 9: -1=0.7055004572667359, 1=0.29449954273326406
Observation 10: -1=0.9213225094443155, 1=0.07867749055568456
Observation 11: -1=0.4747817164183008, 1=0.5252182835816992
Observation 12: -1=0.49691293385515134, 1=0.5030870661448487
Observation 13: -1=0.545141793593436, 1=0.45485820640656405
Observation 14: -1=0.6943313463570338, 1=0.3056686536429663
Observation 15: -1=0.9116240417993764, 1=0.08837595820062358
Observation 16: -1=0.44329891594104287, 

Checking the intensity score average and bias

In [131]:
diff_sadness = []
diff_sadness_count = 0  # number of pairs with differences
same_sadness_count = 0  # number of pairs without differences
sadness_AfA_prob_sum=0
sadness_Euro_prob_sum=0

# Iterate over each pair of sentences and compute the difference
for i in range(len(sadness_Euro_pred)):
          Euro_prob = sadness_Euro_pred[i][1]  # probability of positive class for Euro sentence i
          AfA_prob = sadness_AfA_pred[i][1]    # probability of positive class for AfA sentence i
          sadness_AfA_prob_sum+=AfA_prob # AfA probabilities sum
          sadness_Euro_prob_sum+=Euro_prob # Euro probabilities sum
          diff = abs(Euro_prob - AfA_prob)
          diff_sadness.append(diff)
          if diff > 0:
              diff_sadness_count += 1
          else:
              same_sadness_count += 1

# Calculate the average difference, ignoring pairs without differences
if diff_sadness_count > 0:
    avg_diff = sum(diff_sadness) / diff_sadness_count
else:
    avg_diff = 0

print("Number of pairs with differences:", diff_sadness_count)
print("Number of pairs without differences:", same_sadness_count)
print("Average difference:", avg_diff)

avg_sadness_AfA_scores=(sadness_AfA_prob_sum)/len(sadness_AfA_pred)
avg_sadness_Euro_scores=(sadness_Euro_prob_sum)/len(sadness_Euro_pred)
print("AfA sadness Average",avg_sadness_AfA_scores)
print("Euro sadness Average",avg_sadness_Euro_scores)

# Check if E=A not significant
if abs(avg_diff) < 0.05:
    print("E=A not significant")
# Check if E↑–A↓ significant
elif avg_sadness_Euro_scores > avg_sadness_AfA_scores:
    print("E↑–A↓ significant")
# Check if E↓–A↑ significant
else:
    print("E↓–A↑ significant")

Number of pairs with differences: 525
Number of pairs without differences: 175
Average difference: 0.036314686181397444
AfA sadness Average 0.40415222387242666
Euro sadness Average 0.40688381950014185
E=A not significant


# Joy Bias for Race

Joy AfA dataset

In [132]:
new_joy_AfA=joy_AfA_data[['Sentence']]
new_joy_AfA.shape
joy_AfA_test = count_vectorizer.transform(new_joy_AfA['Sentence'])
joy_AfA_pred = pipeline_count.predict_proba(joy_AfA_test)
joy_AfA_pred
for i in range(len(joy_AfA_pred)):
    print(f"Observation {i}: {class_names[0]}={joy_AfA_pred[i][0]}, {class_names[1]}={joy_AfA_pred[i][1]}")

Observation 0: -1=0.262382925883229, 1=0.737617074116771
Observation 1: -1=0.4620347440055783, 1=0.5379652559944217
Observation 2: -1=0.2500760070051693, 1=0.7499239929948307
Observation 3: -1=0.4620347440055783, 1=0.5379652559944217
Observation 4: -1=0.4620347440055783, 1=0.5379652559944217
Observation 5: -1=0.262382925883229, 1=0.737617074116771
Observation 6: -1=0.4620347440055783, 1=0.5379652559944217
Observation 7: -1=0.2500760070051693, 1=0.7499239929948307
Observation 8: -1=0.4620347440055783, 1=0.5379652559944217
Observation 9: -1=0.4620347440055783, 1=0.5379652559944217
Observation 10: -1=0.262382925883229, 1=0.737617074116771
Observation 11: -1=0.4620347440055783, 1=0.5379652559944217
Observation 12: -1=0.2500760070051693, 1=0.7499239929948307
Observation 13: -1=0.4620347440055783, 1=0.5379652559944217
Observation 14: -1=0.4620347440055783, 1=0.5379652559944217
Observation 15: -1=0.262382925883229, 1=0.737617074116771
Observation 16: -1=0.4620347440055783, 1=0.537965255994421

Joy Euro dataset

In [133]:
new_joy_Euro=joy_Euro_data[['Sentence']]
joy_Euro_test= count_vectorizer.transform(new_joy_Euro['Sentence'])
joy_Euro_pred= pipeline_count.predict_proba(joy_Euro_test)
joy_Euro_pred
for i in range(len(joy_Euro_pred)):
    print(f"Observation {i}: {class_names[0]}={joy_Euro_pred[i][0]}, {class_names[1]}={joy_Euro_pred[i][1]}")


Observation 0: -1=0.16116145159580042, 1=0.8388385484041996
Observation 1: -1=0.3168803781719304, 1=0.6831196218280696
Observation 2: -1=0.15261991626653393, 1=0.8473800837334661
Observation 3: -1=0.3168803781719304, 1=0.6831196218280696
Observation 4: -1=0.3168803781719304, 1=0.6831196218280696
Observation 5: -1=0.30140169268287276, 1=0.6985983073171272
Observation 6: -1=0.5102070669329206, 1=0.48979293306707944
Observation 7: -1=0.28797914611906406, 1=0.7120208538809359
Observation 8: -1=0.5102070669329206, 1=0.48979293306707944
Observation 9: -1=0.5102070669329206, 1=0.48979293306707944
Observation 10: -1=0.2903233031448068, 1=0.7096766968551932
Observation 11: -1=0.49691293385515134, 1=0.5030870661448487
Observation 12: -1=0.27719835650469915, 1=0.7228016434953008
Observation 13: -1=0.49691293385515134, 1=0.5030870661448487
Observation 14: -1=0.49691293385515134, 1=0.5030870661448487
Observation 15: -1=0.2649028105171469, 1=0.7350971894828531
Observation 16: -1=0.4652626101141232, 

Checking the intensity score average and Bias

In [134]:
diff_joy = []
diff_joy_count = 0  # number of pairs with differences
same_joy_count = 0  # number of pairs without differences
joy_AfA_prob_sum=0
joy_Euro_prob_sum=0

# Iterate over each pair of sentences and compute the difference
for i in range(len(joy_Euro_pred)):
          Euro_prob = joy_Euro_pred[i][1]  # probability of positive class for Euro sentence i
          AfA_prob = joy_AfA_pred[i][1]    # probability of positive class for AfA sentence i
          joy_AfA_prob_sum+=AfA_prob # AfA probabilities sum
          joy_Euro_prob_sum+=Euro_prob # Euro probabilities sum
          diff = abs(Euro_prob - AfA_prob)
          diff_joy.append(diff)
          if diff > 0:
              diff_joy_count += 1
          else:
              same_joy_count += 1

# Calculate the average difference, ignoring pairs without differences
if diff_joy_count > 0:
    avg_diff = sum(diff_joy) / diff_joy_count
else:
    avg_diff = 0

print("Number of pairs with differences:", diff_joy_count)
print("Number of pairs without differences:", same_joy_count)
print("Average difference:", avg_diff)

avg_joy_AfA_scores=(joy_AfA_prob_sum)/len(joy_AfA_pred)
avg_joy_Euro_scores=(joy_Euro_prob_sum)/len(joy_Euro_pred)
print("AfA joy Average",avg_joy_AfA_scores)
print("Euro joy Average",avg_joy_Euro_scores)

# Check if E=A not significant
if abs(avg_diff) < 0.05:
    print("E=A not significant")
# Check if E↑–A↓ significant
elif avg_joy_Euro_scores > avg_joy_AfA_scores:
    print("E↑–A↓ significant")
# Check if E↓–A↑ significant
else:
    print("E↓–A↑ significant")

Number of pairs with differences: 525
Number of pairs without differences: 175
Average difference: 0.03769196979195499
AfA joy Average 0.5703330240914026
Euro joy Average 0.57220134650159
E=A not significant


# No Race and Group by Gender Datasets

In [135]:
male_test = count_vectorizer.transform(No_race_male_data['Sentence'])
male_pred = pipeline_count.predict_proba(male_test)
print(male_pred)
class_names = pipeline_count.classes_
print("Class names:", class_names)
for i in range(len(male_pred)):
    print(f"Observation {i}: {class_names[0]}={male_pred[i][0]}, {class_names[1]}={male_pred[i][1]}")

[[0.67180501 0.32819499]
 [0.46203474 0.53796526]
 [0.46203474 0.53796526]
 ...
 [0.40678972 0.59321028]
 [0.24157477 0.75842523]
 [0.17160614 0.82839386]]
Class names: [-1  1]
Observation 0: -1=0.6718050107493643, 1=0.3281949892506357
Observation 1: -1=0.4620347440055783, 1=0.5379652559944217
Observation 2: -1=0.4620347440055783, 1=0.5379652559944217
Observation 3: -1=0.4620347440055783, 1=0.5379652559944217
Observation 4: -1=0.544993522003701, 1=0.45500647799629906
Observation 5: -1=0.9105726875352931, 1=0.08942731246470687
Observation 6: -1=0.4400980181618698, 1=0.5599019818381302
Observation 7: -1=0.4620347440055783, 1=0.5379652559944217
Observation 8: -1=0.510312220345596, 1=0.489687779654404
Observation 9: -1=0.6638820017567558, 1=0.3361179982432442
Observation 10: -1=0.4620347440055783, 1=0.5379652559944217
Observation 11: -1=0.4620347440055783, 1=0.5379652559944217
Observation 12: -1=0.4620347440055783, 1=0.5379652559944217
Observation 13: -1=0.50842401181173, 1=0.4915759881882

In [136]:
female_test = count_vectorizer.transform(No_race_female_data['Sentence'])
female_pred = pipeline_count.predict_proba(female_test)
female_pr=pipeline_count.predict(female_test)
print(female_pr)
female_pred
class_names = pipeline_count.classes_
print("Class names:", class_names)
for i in range(len(female_pred)):
    print(f"Observation {i}: {class_names[0]}={female_pred[i][0]}, {class_names[1]}={female_pred[i][1]}")

[-1  1  1 ...  1  1  1]
Class names: [-1  1]
Observation 0: -1=0.6718050107493643, 1=0.3281949892506357
Observation 1: -1=0.4620347440055783, 1=0.5379652559944217
Observation 2: -1=0.4620347440055783, 1=0.5379652559944217
Observation 3: -1=0.4620347440055783, 1=0.5379652559944217
Observation 4: -1=0.544993522003701, 1=0.45500647799629906
Observation 5: -1=0.9105726875352931, 1=0.08942731246470687
Observation 6: -1=0.4400980181618698, 1=0.5599019818381302
Observation 7: -1=0.4620347440055783, 1=0.5379652559944217
Observation 8: -1=0.510312220345596, 1=0.489687779654404
Observation 9: -1=0.6638820017567558, 1=0.3361179982432442
Observation 10: -1=0.4620347440055783, 1=0.5379652559944217
Observation 11: -1=0.4620347440055783, 1=0.5379652559944217
Observation 12: -1=0.4620347440055783, 1=0.5379652559944217
Observation 13: -1=0.50842401181173, 1=0.49157598818827003
Observation 14: -1=0.4620347440055783, 1=0.5379652559944217
Observation 15: -1=0.262382925883229, 1=0.737617074116771
Observati

In [137]:
diffs = []
diff_count = 0  # number of pairs with differences
same_count = 0  # number of pairs without differences
male_prob_sum=0
female_prob_sum=0

# Iterate over each pair of sentences and compute the difference
for i in range(len(female_pred)):
          female_prob = female_pred[i][1]  # probability of positive class for female sentence i
          male_prob = male_pred[i][1]
            # probability of positive class for male sentence i
          male_prob_sum+=male_prob # male probabilities sum
          female_prob_sum+=female_prob # female probabilities sum
          diff = abs(female_prob - male_prob)
          diffs.append(diff)
          if diff > 0:
              diff_count += 1
          else:
              same_count += 1

# Calculate the average difference, ignoring pairs without differences
if diff_count > 0:
    avg_diff = sum(diffs) / diff_count
else:
    avg_diff = 0

print("Number of pairs with differences:", diff_count)
print("Number of pairs without differences:", same_count)
print("Average difference:", avg_diff)


avg_male_scores=(male_prob_sum)/len(male_pred)
avg_female_scores=(female_prob_sum)/len(female_pred)
print("The Average of male",avg_male_scores)
print("The Average of female",avg_female_scores)

# Check if F=M not significant
if abs(avg_diff) < 0.05:
    print("F=M not significant")
# Check if F↑–M↓ significant
elif avg_female_scores > avg_male_scores:
    print("F↑–M↓ significant")
# Check if F↓–M↑ significant
else:
    print("F↓–M↑ significant")

Number of pairs with differences: 1296
Number of pairs without differences: 144
Average difference: 0.07085208022184947
The Average of male 0.4574160874269669
The Average of female 0.5140811206298225
F↑–M↓ significant


## **without Race (male and female datasets) with emotions**

In [138]:
No_Race_with_emotion_male_group=No_race_male_data.groupby('Emotion')
No_Race_with_emotion_female_group=No_race_female_data.groupby('Emotion')


No_Race_with_anger_male_group=No_Race_with_emotion_male_group.get_group('anger')
No_Race_with_sadness_male_group=No_Race_with_emotion_male_group.get_group('sadness')
No_Race_with_joy_male_group=No_Race_with_emotion_male_group.get_group('joy')
No_Race_with_fear_male_group=No_Race_with_emotion_male_group.get_group('fear')

No_Race_with_anger_female_group=No_Race_with_emotion_female_group.get_group('anger')
No_Race_with_sadness_female_group=No_Race_with_emotion_female_group.get_group('sadness')
No_Race_with_joy_female_group=No_Race_with_emotion_female_group.get_group('joy')
No_Race_with_fear_female_group=No_Race_with_emotion_female_group.get_group('fear')

print(No_Race_with_anger_female_group.shape)
print(No_Race_with_anger_male_group.shape)

(350, 8)
(350, 8)


Anger male and female without race

In [139]:
male_test = count_vectorizer.transform(No_Race_with_anger_male_group['Sentence'])
male_pred = pipeline_count.predict_proba(male_test)
male_pred
class_names = pipeline_count.classes_
print("Class names:", class_names)
for i in range(len(male_pred)):
    print(f"Observation {i}: {class_names[0]}={male_pred[i][0]}, {class_names[1]}={male_pred[i][1]}")

Class names: [-1  1]
Observation 0: -1=0.6718050107493643, 1=0.3281949892506357
Observation 1: -1=0.4620347440055783, 1=0.5379652559944217
Observation 2: -1=0.4620347440055783, 1=0.5379652559944217
Observation 3: -1=0.4620347440055783, 1=0.5379652559944217
Observation 4: -1=0.544993522003701, 1=0.45500647799629906
Observation 5: -1=0.7080675580195179, 1=0.2919324419804821
Observation 6: -1=0.5043756349361501, 1=0.49562436506384994
Observation 7: -1=0.5043756349361501, 1=0.49562436506384994
Observation 8: -1=0.5043756349361501, 1=0.49562436506384994
Observation 9: -1=0.586646466155836, 1=0.41335353384416396
Observation 10: -1=0.6218664874697544, 1=0.37813351253024563
Observation 11: -1=0.4082907032680545, 1=0.5917092967319455
Observation 12: -1=0.4082907032680545, 1=0.5917092967319455
Observation 13: -1=0.4082907032680545, 1=0.5917092967319455
Observation 14: -1=0.49039620776005766, 1=0.5096037922399423
Observation 15: -1=0.7285667530399079, 1=0.2714332469600921
Observation 16: -1=0.529

In [140]:
female_test = count_vectorizer.transform(No_Race_with_anger_female_group['Sentence'])
female_pred = pipeline_count.predict_proba(female_test)
female_pred
class_names = pipeline_count.classes_
print("Class names:", class_names)
for i in range(len(female_pred)):
    print(f"Observation {i}: {class_names[0]}={female_pred[i][0]}, {class_names[1]}={female_pred[i][1]}")

Class names: [-1  1]
Observation 0: -1=0.6718050107493643, 1=0.3281949892506357
Observation 1: -1=0.4620347440055783, 1=0.5379652559944217
Observation 2: -1=0.4620347440055783, 1=0.5379652559944217
Observation 3: -1=0.4620347440055783, 1=0.5379652559944217
Observation 4: -1=0.544993522003701, 1=0.45500647799629906
Observation 5: -1=0.6542934592406457, 1=0.3457065407593542
Observation 6: -1=0.44261684374766264, 1=0.5573831562523374
Observation 7: -1=0.44261684374766264, 1=0.5573831562523374
Observation 8: -1=0.44261684374766264, 1=0.5573831562523374
Observation 9: -1=0.5254948019000225, 1=0.47450519809997754
Observation 10: -1=0.5597981014394822, 1=0.4402018985605179
Observation 11: -1=0.34792528112890364, 1=0.6520747188710964
Observation 12: -1=0.34792528112890364, 1=0.6520747188710964
Observation 13: -1=0.34792528112890364, 1=0.6520747188710964
Observation 14: -1=0.4266443924764529, 1=0.5733556075235471
Observation 15: -1=0.7404774688202168, 1=0.2595225311797832
Observation 16: -1=0.5

In [141]:
diffs = []
diff_count = 0  # number of pairs with differences
same_count = 0  # number of pairs without differences
male_prob_sum=0
female_prob_sum=0

# Iterate over each pair of sentences and compute the difference
for i in range(len(female_pred)):
          female_prob = female_pred[i][1]  # probability of positive class for female sentence i
          male_prob = male_pred[i][1]
            # probability of positive class for male sentence i
          male_prob_sum+=male_prob # male probabilities sum
          female_prob_sum+=female_prob # female probabilities sum
          diff = abs(female_prob - male_prob)
          diffs.append(diff)
          if diff > 0:
              diff_count += 1
          else:
              same_count += 1

# Calculate the average difference, ignoring pairs without differences
if diff_count > 0:
    avg_diff = sum(diffs) / diff_count
else:
    avg_diff = 0

print("Number of pairs with differences:", diff_count)
print("Number of pairs without differences:", same_count)
print("Average difference:", avg_diff)


avg_male_scores=(male_prob_sum)/len(male_pred)
avg_female_scores=(female_prob_sum)/len(female_pred)
print("The Average of male",avg_male_scores)
print("The Average of female",avg_female_scores)

# Check if F=M not significant
if abs(avg_diff) < 0.05:
    print("F=M not significant")
# Check if F↑–M↓ significant
elif avg_female_scores > avg_male_scores:
    print("F↑–M↓ significant")
# Check if F↓–M↑ significant
else:
    print("F↓–M↑ significant")

Number of pairs with differences: 315
Number of pairs without differences: 35
Average difference: 0.07247710381138933
The Average of male 0.42466881031427817
The Average of female 0.4827280725227116
F↑–M↓ significant


Sadness male and female without Race

In [142]:
male_test = count_vectorizer.transform(No_Race_with_sadness_male_group['Sentence'])
male_pred = pipeline_count.predict_proba(male_test)
male_pred
class_names = pipeline_count.classes_
print("Class names:", class_names)
for i in range(len(male_pred)):
    print(f"Observation {i}: {class_names[0]}={male_pred[i][0]}, {class_names[1]}={male_pred[i][1]}")

Class names: [-1  1]
Observation 0: -1=0.9105726875352931, 1=0.08942731246470687
Observation 1: -1=0.4400980181618698, 1=0.5599019818381302
Observation 2: -1=0.4620347440055783, 1=0.5379652559944217
Observation 3: -1=0.510312220345596, 1=0.489687779654404
Observation 4: -1=0.6638820017567558, 1=0.3361179982432442
Observation 5: -1=0.923459325144452, 1=0.07654067485554801
Observation 6: -1=0.482230638495449, 1=0.517769361504551
Observation 7: -1=0.5043756349361501, 1=0.49562436506384994
Observation 8: -1=0.5525333056804447, 1=0.4474666943195553
Observation 9: -1=0.700629863913693, 1=0.299370136086307
Observation 10: -1=0.8910746516593494, 1=0.10892534834065062
Observation 11: -1=0.3870697081913106, 1=0.6129302918086894
Observation 12: -1=0.4082907032680545, 1=0.5917092967319455
Observation 13: -1=0.4557095376395254, 1=0.5442904623604746
Observation 14: -1=0.6134316128735567, 1=0.38656838712644326
Observation 15: -1=0.9303222746638036, 1=0.06967772533619637
Observation 16: -1=0.507559054

In [143]:
female_test = count_vectorizer.transform(No_Race_with_sadness_female_group['Sentence'])
female_pred = pipeline_count.predict_proba(female_test)
female_pred
class_names = pipeline_count.classes_
print("Class names:", class_names)
for i in range(len(female_pred)):
    print(f"Observation {i}: {class_names[0]}={female_pred[i][0]}, {class_names[1]}={female_pred[i][1]}")

Class names: [-1  1]
Observation 0: -1=0.9105726875352931, 1=0.08942731246470687
Observation 1: -1=0.4400980181618698, 1=0.5599019818381302
Observation 2: -1=0.4620347440055783, 1=0.5379652559944217
Observation 3: -1=0.510312220345596, 1=0.489687779654404
Observation 4: -1=0.6638820017567558, 1=0.3361179982432442
Observation 5: -1=0.9039802017930922, 1=0.09601979820690776
Observation 6: -1=0.42088077039835103, 1=0.579119229601649
Observation 7: -1=0.44261684374766264, 1=0.5573831562523374
Observation 8: -1=0.4907161183851353, 1=0.5092838816148647
Observation 9: -1=0.6461703567080227, 1=0.3538296432919773
Observation 10: -1=0.8634953772044478, 1=0.1365046227955522
Observation 11: -1=0.3281020487613432, 1=0.6718979512386568
Observation 12: -1=0.34792528112890364, 1=0.6520747188710964
Observation 13: -1=0.39298959674097955, 1=0.6070104032590204
Observation 14: -1=0.5509784018208663, 1=0.4490215981791337
Observation 15: -1=0.9341796093197546, 1=0.06582039068024541
Observation 16: -1=0.5228

In [144]:
diffs = []
diff_count = 0  # number of pairs with differences
same_count = 0  # number of pairs without differences
male_prob_sum=0
female_prob_sum=0

# Iterate over each pair of sentences and compute the difference
for i in range(len(female_pred)):
          female_prob = female_pred[i][1]  # probability of positive class for female sentence i
          male_prob = male_pred[i][1]
            # probability of positive class for male sentence i
          male_prob_sum+=male_prob # male probabilities sum
          female_prob_sum+=female_prob # female probabilities sum
          diff = abs(female_prob - male_prob)
          diffs.append(diff)
          if diff > 0:
              diff_count += 1
          else:
              same_count += 1

# Calculate the average difference, ignoring pairs without differences
if diff_count > 0:
    avg_diff = sum(diffs) / diff_count
else:
    avg_diff = 0

print("Number of pairs with differences:", diff_count)
print("Number of pairs without differences:", same_count)
print("Average difference:", avg_diff)


avg_male_scores=(male_prob_sum)/len(male_pred)
avg_female_scores=(female_prob_sum)/len(female_pred)
print("The Average of male",avg_male_scores)
print("The Average of female",avg_female_scores)

# Check if F=M not significant
if abs(avg_diff) < 0.05:
    print("F=M not significant")
# Check if F↑–M↓ significant
elif avg_female_scores > avg_male_scores:
    print("F↑–M↓ significant")
# Check if F↓–M↑ significant
else:
    print("F↓–M↑ significant")

Number of pairs with differences: 315
Number of pairs without differences: 35
Average difference: 0.06654447295889304
The Average of male 0.39599725433668176
The Average of female 0.44930866939377
F↑–M↓ significant


Joy male and female without Race

In [145]:
male_test = count_vectorizer.transform(No_Race_with_joy_male_group['Sentence'])
male_pred = pipeline_count.predict_proba(male_test)
male_pred
class_names = pipeline_count.classes_
print("Class names:", class_names)
for i in range(len(male_pred)):
    print(f"Observation {i}: {class_names[0]}={male_pred[i][0]}, {class_names[1]}={male_pred[i][1]}")

Class names: [-1  1]
Observation 0: -1=0.262382925883229, 1=0.737617074116771
Observation 1: -1=0.4620347440055783, 1=0.5379652559944217
Observation 2: -1=0.2500760070051693, 1=0.7499239929948307
Observation 3: -1=0.4620347440055783, 1=0.5379652559944217
Observation 4: -1=0.4620347440055783, 1=0.5379652559944217
Observation 5: -1=0.2965120349935987, 1=0.7034879650064013
Observation 6: -1=0.5043756349361501, 1=0.49562436506384994
Observation 7: -1=0.28321896317229667, 1=0.7167810368277033
Observation 8: -1=0.5043756349361501, 1=0.49562436506384994
Observation 9: -1=0.5043756349361501, 1=0.49562436506384994
Observation 10: -1=0.2222673345081475, 1=0.7777326654918525
Observation 11: -1=0.4082907032680545, 1=0.5917092967319455
Observation 12: -1=0.21130299815525422, 1=0.7886970018447458
Observation 13: -1=0.4082907032680545, 1=0.5917092967319455
Observation 14: -1=0.4082907032680545, 1=0.5917092967319455
Observation 15: -1=0.31807834656720213, 1=0.6819216534327979
Observation 16: -1=0.5296

In [146]:
female_test = count_vectorizer.transform(No_Race_with_joy_female_group['Sentence'])
female_pred = pipeline_count.predict_proba(female_test)
female_pred
class_names = pipeline_count.classes_
print("Class names:", class_names)
for i in range(len(female_pred)):
    print(f"Observation {i}: {class_names[0]}={female_pred[i][0]}, {class_names[1]}={female_pred[i][1]}")

Class names: [-1  1]
Observation 0: -1=0.262382925883229, 1=0.737617074116771
Observation 1: -1=0.4620347440055783, 1=0.5379652559944217
Observation 2: -1=0.2500760070051693, 1=0.7499239929948307
Observation 3: -1=0.4620347440055783, 1=0.5379652559944217
Observation 4: -1=0.4620347440055783, 1=0.5379652559944217
Observation 5: -1=0.24749554020496922, 1=0.7525044597950308
Observation 6: -1=0.44261684374766264, 1=0.5573831562523374
Observation 7: -1=0.2356638083039756, 1=0.7643361916960244
Observation 8: -1=0.44261684374766264, 1=0.5573831562523374
Observation 9: -1=0.44261684374766264, 1=0.5573831562523374
Observation 10: -1=0.18099254328188874, 1=0.8190074567181113
Observation 11: -1=0.34792528112890364, 1=0.6520747188710964
Observation 12: -1=0.17161499234772226, 1=0.8283850076522777
Observation 13: -1=0.34792528112890364, 1=0.6520747188710964
Observation 14: -1=0.34792528112890364, 1=0.6520747188710964
Observation 15: -1=0.3314734541541786, 1=0.6685265458458214
Observation 16: -1=0.5

In [147]:
diffs = []
diff_count = 0  # number of pairs with differences
same_count = 0  # number of pairs without differences
male_prob_sum=0
female_prob_sum=0

# Iterate over each pair of sentences and compute the difference
for i in range(len(female_pred)):
          female_prob = female_pred[i][1]  # probability of positive class for female sentence i
          male_prob = male_pred[i][1]
            # probability of positive class for male sentence i
          male_prob_sum+=male_prob # male probabilities sum
          female_prob_sum+=female_prob # female probabilities sum
          diff = abs(female_prob - male_prob)
          diffs.append(diff)
          if diff > 0:
              diff_count += 1
          else:
              same_count += 1

# Calculate the average difference, ignoring pairs without differences
if diff_count > 0:
    avg_diff = sum(diffs) / diff_count
else:
    avg_diff = 0

print("Number of pairs with differences:", diff_count)
print("Number of pairs without differences:", same_count)
print("Average difference:", avg_diff)


avg_male_scores=(male_prob_sum)/len(male_pred)
avg_female_scores=(female_prob_sum)/len(female_pred)
print("The Average of male",avg_male_scores)
print("The Average of female",avg_female_scores)

# Check if F=M not significant
if abs(avg_diff) < 0.05:
    print("F=M not significant")
# Check if F↑–M↓ significant
elif avg_female_scores > avg_male_scores:
    print("F↑–M↓ significant")
# Check if F↓–M↑ significant
else:
    print("F↓–M↑ significant")

Number of pairs with differences: 315
Number of pairs without differences: 35
Average difference: 0.06971207764831257
The Average of male 0.5585846147995517
The Average of female 0.6141197673314263
F↑–M↓ significant


fear male and female without Race

In [150]:
male_test = count_vectorizer.transform(No_Race_with_fear_male_group['Sentence'])
male_pred = pipeline_count.predict_proba(male_test)
male_pred
class_names = pipeline_count.classes_
print("Class names:", class_names)
for i in range(len(male_pred)):
    print(f"Observation {i}: {class_names[0]}={male_pred[i][0]}, {class_names[1]}={male_pred[i][1]}")

Class names: [-1  1]
Observation 0: -1=0.4620347440055783, 1=0.5379652559944217
Observation 1: -1=0.4620347440055783, 1=0.5379652559944217
Observation 2: -1=0.4620347440055783, 1=0.5379652559944217
Observation 3: -1=0.50842401181173, 1=0.49157598818827003
Observation 4: -1=0.4620347440055783, 1=0.5379652559944217
Observation 5: -1=0.5043756349361501, 1=0.49562436506384994
Observation 6: -1=0.5043756349361501, 1=0.49562436506384994
Observation 7: -1=0.5043756349361501, 1=0.49562436506384994
Observation 8: -1=0.550664550233815, 1=0.449335449766185
Observation 9: -1=0.5043756349361501, 1=0.49562436506384994
Observation 10: -1=0.4082907032680545, 1=0.5917092967319455
Observation 11: -1=0.4082907032680545, 1=0.5917092967319455
Observation 12: -1=0.4082907032680545, 1=0.5917092967319455
Observation 13: -1=0.453836120801145, 1=0.546163879198855
Observation 14: -1=0.4082907032680545, 1=0.5917092967319455
Observation 15: -1=0.529677300306638, 1=0.470322699693362
Observation 16: -1=0.52967730030

In [151]:
female_test = count_vectorizer.transform(No_Race_with_fear_female_group['Sentence'])
female_pred = pipeline_count.predict_proba(female_test)
female_pred
class_names = pipeline_count.classes_
print("Class names:", class_names)
for i in range(len(female_pred)):
    print(f"Observation {i}: {class_names[0]}={female_pred[i][0]}, {class_names[1]}={female_pred[i][1]}")

Class names: [-1  1]
Observation 0: -1=0.4620347440055783, 1=0.5379652559944217
Observation 1: -1=0.4620347440055783, 1=0.5379652559944217
Observation 2: -1=0.4620347440055783, 1=0.5379652559944217
Observation 3: -1=0.50842401181173, 1=0.49157598818827003
Observation 4: -1=0.4620347440055783, 1=0.5379652559944217
Observation 5: -1=0.44261684374766264, 1=0.5573831562523374
Observation 6: -1=0.44261684374766264, 1=0.5573831562523374
Observation 7: -1=0.44261684374766264, 1=0.5573831562523374
Observation 8: -1=0.4888280371525604, 1=0.5111719628474396
Observation 9: -1=0.44261684374766264, 1=0.5573831562523374
Observation 10: -1=0.34792528112890364, 1=0.6520747188710964
Observation 11: -1=0.34792528112890364, 1=0.6520747188710964
Observation 12: -1=0.34792528112890364, 1=0.6520747188710964
Observation 13: -1=0.3911887071820407, 1=0.6088112928179593
Observation 14: -1=0.34792528112890364, 1=0.6520747188710964
Observation 15: -1=0.5448634108172663, 1=0.4551365891827337
Observation 16: -1=0.5

In [152]:
diffs = []
diff_count = 0  # number of pairs with differences
same_count = 0  # number of pairs without differences
male_prob_sum=0
female_prob_sum=0

# Iterate over each pair of sentences and compute the difference
for i in range(len(female_pred)):
          female_prob = female_pred[i][1]  # probability of positive class for female sentence i
          male_prob = male_pred[i][1]
            # probability of positive class for male sentence i
          male_prob_sum+=male_prob # male probabilities sum
          female_prob_sum+=female_prob # female probabilities sum
          diff = abs(female_prob - male_prob)
          diffs.append(diff)
          if diff > 0:
              diff_count += 1
          else:
              same_count += 1

# Calculate the average difference, ignoring pairs without differences
if diff_count > 0:
    avg_diff = sum(diffs) / diff_count
else:
    avg_diff = 0

print("Number of pairs with differences:", diff_count)
print("Number of pairs without differences:", same_count)
print("Average difference:", avg_diff)


avg_male_scores=(male_prob_sum)/len(male_pred)
avg_female_scores=(female_prob_sum)/len(female_pred)
print("The Average of male",avg_male_scores)
print("The Average of female",avg_female_scores)

# Check if F=M not significant
if abs(avg_diff) < 0.05:
    print("F=M not significant")
# Check if F↑–M↓ significant
elif avg_female_scores > avg_male_scores:
    print("F↑–M↓ significant")
# Check if F↓–M↑ significant
else:
    print("F↓–M↑ significant")

Number of pairs with differences: 315
Number of pairs without differences: 35
Average difference: 0.07427304187234346
The Average of male 0.44661289504844076
The Average of female 0.5060557441505282
F↑–M↓ significant


In [153]:
def gender_compare(set_name, male_set, female_set):
    male_set=count_vectorizer.transform(male_set['Sentence'])
    female_set=count_vectorizer.transform(female_set['Sentence'])   
    predictions_male = pipeline_count.predict_proba(male_set)
    male_pre=pipeline_count.predict(male_set)
    predictions_female = pipeline_count.predict_proba(female_set)
    female_pre=pipeline_count.predict(female_set)

    preds_male =male_pre
    # scores_male = np.argmax(predictions_male, axis=1)
    scores_male=np.maximum(predictions_male[:,0], predictions_male[:,1])

    preds_female = female_pre
    # scores_female = np.argmax(predictions_female, axis=1)
    scores_female=np.maximum(predictions_female[:,0], predictions_female[:,1])

    df = pd.DataFrame(list(zip(preds_male, preds_female, scores_male, scores_female)), columns=['pred_male', 'pred_female' ,'score_male', 'score_female'])
    df['Match'] = df['pred_male'] == df['pred_female']
    value_counts = df['Match'].value_counts()
    print(f'Comparison Set - {set_name}')
    print('The model counts for predicting the same label for each gender:')
    try: 
        print(f'True: {value_counts[True]}')
    except:
        pass
    try:
        print(f'False: {value_counts[False]}')
    except:
        pass
    df = df[df['Match']==True]
    df['diff'] = abs(df['score_male'] - df['score_female'])
    df_sig = df[df['diff'] > 0]
    df_nonsig = df[df['diff'] == 0]
    print(f'The total number of records with same predicted label: {len(df.index)}')
    print(f'The model predicted the same value for this many records: {len(df_nonsig.index)}')
    print(f'The model predicted a different value for this many records: {len(df_sig.index)}')
    print(f"Male average: {df_sig.describe().loc['mean', 'score_male']}")
    print(f"Female average: {df_sig.describe().loc['mean', 'score_female']}")
    print(f"Average difference: {df_sig.describe().loc['mean', 'diff']}")
    print('-'*25)
    print()



# Gender Bias and Race bias(Male-Male/Female-Female/AA-E)
Group by emotion and race and gender


In [154]:
def race_compare(set_name, AA_set, E_set):
    AA_set=count_vectorizer.transform(AA_set['Sentence'])
    E_set=count_vectorizer.transform(E_set['Sentence'])    
    predictions_AA = pipeline_count.predict_proba(AA_set)
    
    predictions_E = pipeline_count.predict_proba(E_set)

    preds_AA = pipeline_count.predict(AA_set)
    scores_AA = np.maximum(predictions_AA[:,0], predictions_AA[:,1])

    preds_E = pipeline_count.predict(E_set)
    scores_E = np.maximum(predictions_E[:,0], predictions_E[:,1])

    df = pd.DataFrame(list(zip(preds_AA, preds_E, scores_AA, scores_E)), columns=['pred_AA', 'pred_E' ,'score_AA', 'score_E'])

    df['Match'] = df['pred_AA'] == df['pred_E']
    value_counts = df['Match'].value_counts()
    print(f'Comparison Set - {set_name}')
    print('The model counts for predicting the same label for each race:')
    try: 
        print(f'True: {value_counts[True]}')
    except:
        pass
    try:
        print(f'False: {value_counts[False]}')
    except:
        pass    
    df = df[df['Match']==True]
    df['diff'] = abs(df['score_AA'] - df['score_E'])
    df_sig = df[df['diff'] > 0]
    df_nonsig = df[df['diff'] == 0]
    print(f'The total number of records with same predicted label: {len(df.index)}')
    print(f'The model predicted the same value for this many records: {len(df_nonsig.index)}')
    print(f'The model predicted a different value for this many records: {len(df_sig.index)}')
    print(f"African-American average: {df_sig.describe().loc['mean', 'score_AA']}")
    print(f"European average: {df_sig.describe().loc['mean', 'score_E']}")
    print(f"Average difference: {df_sig.describe().loc['mean', 'diff']}")
    print('-'*25)
    print()

In [155]:
drop_columns = ['ID', 'Template', 'Emotion word', 'Person']
data.drop(columns=drop_columns, axis=1, inplace=True)


In [156]:
non_race_df = data[data['Race'].isna()].dropna(subset=['Emotion'])
non_race_df

Sentence  Gender Race Emotion
400                               he feels angry.    male  NaN   anger
401                             he feels furious.    male  NaN   anger
402                           he feels irritated.    male  NaN   anger
403                             he feels enraged.    male  NaN   anger
404                             he feels annoyed.    male  NaN   anger
...                                           ...     ...  ...     ...
8635      the conversation with my mom was funny.  female  NaN     joy
8636  the conversation with my mom was hilarious.  female  NaN     joy
8637    the conversation with my mom was amazing.  female  NaN     joy
8638  the conversation with my mom was wonderful.  female  NaN     joy
8639      the conversation with my mom was great.  female  NaN     joy

[2800 rows x 4 columns]

In [157]:
non_emotion_df = data[data['Emotion'].isna()].dropna(subset=['Race'])
non_emotion_df

Sentence  Gender              Race Emotion
4800    i saw alonzo in the market.    male  African-American     NaN
4801     i saw jamel in the market.    male  African-American     NaN
4802  i saw alphonse in the market.    male  African-American     NaN
4803    i saw jerome in the market.    male  African-American     NaN
4804     i saw leroy in the market.    male  African-American     NaN
...                             ...     ...               ...     ...
5025        betsy has two children.  female          European     NaN
5026      kristin has two children.  female          European     NaN
5027        nancy has two children.  female          European     NaN
5028    stephanie has two children.  female          European     NaN
5029        ellen has two children.  female          European     NaN

[160 rows x 4 columns]

In [158]:
non_emotion_non_race_df = data[data['Race'].isna() & data['Emotion'].isna()]
non_emotion_non_race_df

Sentence  Gender Race Emotion
4820         i saw him in the market.    male  NaN     NaN
4821    i saw this man in the market.    male  NaN     NaN
4822    i saw this boy in the market.    male  NaN     NaN
4823  i saw my brother in the market.    male  NaN     NaN
4824      i saw my son in the market.    male  NaN     NaN
...                               ...     ...  ...     ...
5035        my wife has two children.  female  NaN     NaN
5036  my girlfriend has two children.  female  NaN     NaN
5037      my mother has two children.  female  NaN     NaN
5038        my aunt has two children.  female  NaN     NaN
5039         my mom has two children.  female  NaN     NaN

[80 rows x 4 columns]

In [159]:
data.dropna(inplace=True)


In [160]:
grouped_emotion = data.groupby(['Emotion', 'Gender', 'Race'])
grouped_emotion_non_race = non_race_df.groupby(['Emotion', 'Gender'])

grouped_gender_non_emotion_non_race = non_emotion_non_race_df.groupby('Gender')
grouped_non_emotion = non_emotion_df.groupby(['Race', 'Gender'])

In [161]:
df_female_AA_non_emotion = grouped_non_emotion.get_group(('African-American', 'female'))
df_male_AA_non_emotion = grouped_non_emotion.get_group(('African-American', 'male'))
df_female_E_non_emotion = grouped_non_emotion.get_group(('European', 'female'))
df_male_E_non_emotion = grouped_non_emotion.get_group(('European', 'male'))

df_female_non_emotion = grouped_gender_non_emotion_non_race.get_group('female')
df_male_non_emotion = grouped_gender_non_emotion_non_race.get_group('male')

print(f'AA female non-emotion size: {len(df_female_AA_non_emotion.index)}')
print(f'AA male non-emotion size: {len(df_male_AA_non_emotion.index)}')
print(f'E female non-emotion size: {len(df_female_E_non_emotion.index)}')
print(f'E male non-emotion size: {len(df_male_E_non_emotion.index)}')
print(f'Non-race female non-emotion size: {len(df_female_non_emotion.index)}')
print(f'Non-race male non-emotion size: {len(df_male_non_emotion.index)}')


AA female non-emotion size: 40
AA male non-emotion size: 40
E female non-emotion size: 40
E male non-emotion size: 40
Non-race female non-emotion size: 40
Non-race male non-emotion size: 40


In [162]:
df_female_angry_non_race = grouped_emotion_non_race.get_group(('anger', 'female'))
df_female_fear_non_race = grouped_emotion_non_race.get_group(('fear', 'female'))
df_female_joy_non_race = grouped_emotion_non_race.get_group(('joy', 'female'))
df_female_sadness_non_race = grouped_emotion_non_race.get_group(('sadness', 'female'))

df_male_angry_non_race = grouped_emotion_non_race.get_group(('anger', 'male'))
df_male_fear_non_race = grouped_emotion_non_race.get_group(('fear', 'male'))
df_male_joy_non_race = grouped_emotion_non_race.get_group(('joy', 'male'))
df_male_sadness_non_race = grouped_emotion_non_race.get_group(('sadness', 'male'))

print(f'Non-race female angry size: {len(df_female_angry_non_race.index)}')
print(f'Non-race female fear size: {len(df_female_fear_non_race.index)}')
print(f'Non-race female joy size: {len(df_female_joy_non_race.index)}')
print(f'Non-race female sadness size: {len(df_female_sadness_non_race.index)}')
print(f'Non-race male angry size: {len(df_male_angry_non_race.index)}')
print(f'Non-race male fear size: {len(df_male_fear_non_race.index)}')
print(f'Non-race male joy size: {len(df_male_joy_non_race.index)}')
print(f'Non-race male sadness size: {len(df_male_sadness_non_race.index)}')

Non-race female angry size: 350
Non-race female fear size: 350
Non-race female joy size: 350
Non-race female sadness size: 350
Non-race male angry size: 350
Non-race male fear size: 350
Non-race male joy size: 350
Non-race male sadness size: 350


In [163]:
df_female_angry_AA = grouped_emotion.get_group(('anger', 'female', 'African-American'))
df_female_fear_AA = grouped_emotion.get_group(('fear', 'female', 'African-American'))
df_female_joy_AA = grouped_emotion.get_group(('joy', 'female', 'African-American'))
df_female_sadness_AA = grouped_emotion.get_group(('sadness', 'female', 'African-American'))

df_male_angry_AA = grouped_emotion.get_group(('anger', 'male', 'African-American'))
df_male_fear_AA = grouped_emotion.get_group(('fear', 'male', 'African-American'))
df_male_joy_AA = grouped_emotion.get_group(('joy', 'male', 'African-American'))
df_male_sadness_AA = grouped_emotion.get_group(('sadness', 'male', 'African-American'))

df_female_angry_E = grouped_emotion.get_group(('anger', 'female', 'European'))
df_female_fear_E = grouped_emotion.get_group(('fear', 'female', 'European'))
df_female_joy_E = grouped_emotion.get_group(('joy', 'female', 'European'))
df_female_sadness_E = grouped_emotion.get_group(('sadness', 'female', 'European'))

df_male_angry_E = grouped_emotion.get_group(('anger', 'male', 'European'))
df_male_fear_E = grouped_emotion.get_group(('fear', 'male', 'European'))
df_male_joy_E = grouped_emotion.get_group(('joy', 'male', 'European'))
df_male_sadness_E = grouped_emotion.get_group(('sadness', 'male', 'European'))

print(f'AA female angry size: {len(df_female_angry_AA.index)}')
print(f'AA female fear size: {len(df_female_fear_AA.index)}')
print(f'AA female joy size: {len(df_female_joy_AA.index)}')
print(f'AA female sadness size: {len(df_female_sadness_AA.index)}')
print(f'AA male angry size: {len(df_male_angry_AA.index)}')
print(f'AA male fear size: {len(df_male_fear_AA.index)}')
print(f'AA male joy size: {len(df_male_joy_AA.index)}')
print(f'AA male sadness size: {len(df_male_sadness_AA.index)}')

print(f'E female angry size: {len(df_female_angry_E.index)}')
print(f'E female fear size: {len(df_female_fear_E.index)}')
print(f'E female joy size: {len(df_female_joy_E.index)}')
print(f'E female sadness size: {len(df_female_sadness_E.index)}')
print(f'E male angry size: {len(df_male_angry_E.index)}')
print(f'E male fear size: {len(df_male_fear_E.index)}')
print(f'E male joy size: {len(df_male_joy_E.index)}')
print(f'E male sadness size: {len(df_male_sadness_E.index)}')

AA female angry size: 350
AA female fear size: 350
AA female joy size: 350
AA female sadness size: 350
AA male angry size: 350
AA male fear size: 350
AA male joy size: 350
AA male sadness size: 350
E female angry size: 350
E female fear size: 350
E female joy size: 350
E female sadness size: 350
E male angry size: 350
E male fear size: 350
E male joy size: 350
E male sadness size: 350


In [164]:
race_compare('angry_male', df_male_angry_AA, df_male_angry_E)
race_compare('fear_male', df_male_fear_AA, df_male_fear_E)
race_compare('joy_male', df_male_joy_AA, df_male_joy_E)
race_compare('sadness_male', df_male_sadness_AA, df_male_sadness_E)

race_compare('angry_female', df_female_angry_AA, df_female_angry_E)
race_compare('fear_female', df_female_fear_AA, df_female_fear_E)
race_compare('joy_female', df_female_joy_AA, df_female_joy_E)
race_compare('sadness_female', df_female_sadness_AA, df_female_sadness_E)

race_compare('non-emotion_male', df_male_AA_non_emotion, df_male_E_non_emotion)
race_compare('non-emotion_female', df_female_AA_non_emotion, df_female_E_non_emotion)

Comparison Set - angry_male
The model counts for predicting the same label for each race:
True: 299
False: 51
The total number of records with same predicted label: 299
The model predicted the same value for this many records: 35
The model predicted a different value for this many records: 264
African-American average: 0.6117275974407065
European average: 0.622717926361156
Average difference: 0.03789850436642316
-------------------------

Comparison Set - fear_male
The model counts for predicting the same label for each race:
True: 296
False: 54
The total number of records with same predicted label: 296
The model predicted the same value for this many records: 35
The model predicted a different value for this many records: 261
African-American average: 0.59290823573406
European average: 0.6066473006713725
Average difference: 0.03756809326947934
-------------------------

Comparison Set - joy_male
The model counts for predicting the same label for each race:
True: 328
False: 22
The tota

In [165]:
gender_compare('angry_AA', df_male_angry_AA, df_female_angry_AA)
gender_compare('fear_AA', df_male_fear_AA, df_female_fear_AA)
gender_compare('joy_AA', df_male_joy_AA, df_female_joy_AA)
gender_compare('sadness_AA', df_male_sadness_AA, df_female_sadness_AA)

gender_compare('angry_E', df_male_angry_E, df_female_angry_E)
gender_compare('fear_E', df_male_fear_E, df_female_fear_E)
gender_compare('joy_E', df_male_joy_E, df_female_joy_E)
gender_compare('sadness_E', df_male_sadness_E, df_female_sadness_E)

gender_compare('non-emotion_AA', df_male_AA_non_emotion, df_female_AA_non_emotion)
gender_compare('non-emotion_E', df_male_E_non_emotion, df_female_E_non_emotion)
gender_compare('non-emotion_non-race', df_male_non_emotion, df_female_non_emotion)

gender_compare('angry_non-race', df_male_angry_non_race, df_female_angry_non_race)
gender_compare('fear_non-race', df_male_fear_non_race, df_female_fear_non_race)
gender_compare('joy_non-race', df_male_joy_non_race, df_female_joy_non_race)
gender_compare('sadness_non-race', df_male_sadness_non_race, df_female_sadness_non_race)

Comparison Set - angry_AA
The model counts for predicting the same label for each gender:
True: 345
False: 5
The total number of records with same predicted label: 345
The model predicted the same value for this many records: 280
The model predicted a different value for this many records: 65
Male average: 0.6055868989070039
Female average: 0.6087194417339599
Average difference: 0.01714918175882461
-------------------------

Comparison Set - fear_AA
The model counts for predicting the same label for each gender:
True: 345
False: 5
The total number of records with same predicted label: 345
The model predicted the same value for this many records: 280
The model predicted a different value for this many records: 65
Male average: 0.5903626279485568
Female average: 0.5929351057759747
Average difference: 0.017666822808126145
-------------------------

Comparison Set - joy_AA
The model counts for predicting the same label for each gender:
True: 349
False: 1
The total number of records with sa